###**Previous Code**

In [35]:
import os
import pandas as pd

"""Summary Compensation Table (SCT) extraction via XPath (core logic).

This module ports the XPath-first strategy from your legacy
scripts/SEC_Documents/Compiling_functions.py with small, well-documented
helpers and safe defaults.

Main entry points:
- extract_sct_tables_from_bytes(html_bytes) -> List[pd.DataFrame]
- extract_sct_tables_from_file(path) -> List[pd.DataFrame]

Notes
- We return a list of candidate tables; caller decides how to persist.
- Cleaning mirrors the legacy behavior: flatten headers, strip strings,
  drop empty columns, dedupe columns.
"""
from __future__ import annotations

from typing import List
from pathlib import Path

import pandas as pd
from lxml import html as LH  # type: ignore
import re


def _flatten_columns(df: pd.DataFrame) -> pd.DataFrame:
    if isinstance(df.columns, pd.MultiIndex):
        df.columns = [
            " ".join([str(x) for x in col if "Unnamed" not in str(x)]).strip()
            for col in df.columns.values
        ]
    else:
        df.columns = [str(c).strip() for c in df.columns]
    return df


def _strip_cells(df: pd.DataFrame) -> pd.DataFrame:
    # map over all cells
    return df.map(lambda x: x.strip() if isinstance(x, str) else x)


def process_extracted_table(table_el) -> pd.DataFrame:
    """Convert an lxml <table> element into a cleaned DataFrame."""
    df_list = pd.read_html(LH.tostring(table_el))
    if not df_list:
        return pd.DataFrame()
    df = df_list[0]
    df = _flatten_columns(df)
    df = _strip_cells(df)
    df = df.dropna(axis=1, how="all")
    df = df.dropna(axis=0, how="all")
    # Remove duplicate column names (keep first)
    df = df.loc[:, ~df.columns.duplicated()]
    # Apply deterministic normalization to standardize and consolidate columns
    df = normalize_sct_dataframe(df)
    return df


def normalize_sct_dataframe(df: pd.DataFrame) -> pd.DataFrame:
    """Normalize SCT DataFrame headers and consolidate duplicate logical columns.

    - Detects when the first row contains real headers (generic/Unnamed columns case)
    - Standardizes common SCT column names (salary, bonus, stock_awards, etc.)
    - Consolidates duplicates by preferring series with more numeric content
    - Drops all-empty cols/rows and duplicate rows
    """
    if df.empty:
        return df

    # If the very first row is all-NaN, drop it early (junk row from read_html)
    if len(df) and df.iloc[0].isna().all():
        df = df.iloc[1:].reset_index(drop=True)

    # Determine if current columns look generic (e.g., Unnamed or plain digits)
    orig_columns = list(df.columns)
    cols_as_str = [str(c) for c in orig_columns]
    looks_generic = all(re.match(r"^(Unnamed.*|\d+)$", c) for c in cols_as_str)

    if looks_generic and len(df) > 0:
        # Promote first row to header text; keep mapping by original column labels
        header_row = df.iloc[0].astype(str).str.replace(r"\n|\r", "", regex=True).str.strip()
        header_row.index = pd.Index(orig_columns)
        data_df = df.iloc[1:].reset_index(drop=True)
        header_by_label = header_row
    else:
        # Use existing column labels as header texts
        data_df = df.reset_index(drop=True)
        ser = pd.Series([str(c) for c in data_df.columns], index=data_df.columns)
        header_by_label = ser

    # Drop columns that are entirely NaN and remove fully-empty first-column rows
    data_df = data_df.dropna(axis=1, how="all")
    if data_df.shape[1] == 0:
        return data_df
    # Ensure there's a first column to check for empties
    data_df = data_df[data_df.iloc[:, 0].notna()].reset_index(drop=True)

    # Drop symbol-only columns (e.g., columns with only '$', dashes, punctuation)
    def _is_symbol_only_col(s: pd.Series) -> bool:
        if s is None:
            return False
        vals = s.dropna().astype(str).str.strip().str.replace("\u00a0", "", regex=False)
        if vals.empty:
            return False  # already handled by dropna(all)
        # True if every non-null cell contains no letters or digits
        return bool((~vals.str.contains(r"[A-Za-z0-9]", regex=True)).all())

    keep_cols = []
    for c in list(data_df.columns):
        if _is_symbol_only_col(data_df[c]):
            continue
        keep_cols.append(c)
    if len(keep_cols) != len(data_df.columns):
        data_df = data_df[keep_cols]

    # Mapping for canonical SCT columns (aligned with AI pipeline expectations)
    column_mapping = {
        'salary': ['salary'],
        'bonus': ['bonus'],
        'stock_awards': ['stock awards', 'stock-awards'],
        'option_awards': ['option awards', 'option-awards'],
        'non_equity_incentive_plan': [
            'non-equity incentive plan compensation',
            'non-equity incentive',
            'non equity incentive',
        ],
        'pension_value': ['change in pension', 'pension value', 'deferred compensation compensation'],
        'all_other_compensation': ['all other compensation', 'all other comp'],
        'total': ['total salary and incentive compensation', 'total'],
        'year': ['year', 'fiscal year ended'],
        'name_position': ['name and principal position', 'name & principal position', 'principal position', 'name'],
    }

    def clean_string_for_matching(text: str) -> str:
        t = str(text).lower().strip()
        t = re.sub(r"\s*\([^)]*\)", "", t)  # drop parentheticals
        t = re.sub(r"[^a-z0-9 ]", "", t)      # keep alnum + spaces
        t = re.sub(r"\s+", " ", t).strip()
        return t.replace(" ", "")

    reverse_mapping = {}
    for std, variants in column_mapping.items():
        for v in variants:
            reverse_mapping[clean_string_for_matching(v)] = std

    def normalize_column_name(name: str) -> str:
        key = clean_string_for_matching(name)
        if key in reverse_mapping:
            return reverse_mapping[key]
        # Fallbacks
        if 'salary' in key:
            return 'salary'
        if 'bonus' in key:
            return 'bonus'
        if 'stockaward' in key:
            return 'stock_awards'
        if 'optionaward' in key:
            return 'option_awards'
        if 'incentive' in key:
            return 'non_equity_incentive_plan'
        if 'pension' in key:
            return 'pension_value'
        if 'othercomp' in key or 'allother' in key:
            return 'all_other_compensation'
        if 'total' in key:
            return 'total'
        if 'year' in key:
            return 'year'
        if 'nameprincipalposition' in key or 'principalposition' in key or key == 'name':
            return 'name_position'
        return str(name)

    # Consolidate columns by normalized name; prefer series with more numeric content
    final_cols: dict[str, pd.Series] = {}
    for col_label in list(data_df.columns):
        header_text = header_by_label.get(col_label, str(col_label))
        norm = normalize_column_name(header_text)
        series = data_df[col_label].reset_index(drop=True)

        if norm not in final_cols:
            final_cols[norm] = series
            continue

        def as_numeric(s: pd.Series) -> pd.Series:
            s = s.astype(str).str.replace('$', '', regex=False) \
                         .str.replace(',', '', regex=False) \
                         .str.replace('—', '', regex=False) \
                         .str.replace('(', '-', regex=False) \
                         .str.replace(')', '', regex=False) \
                         .str.strip()
            return pd.to_numeric(s, errors='coerce')

        existing = final_cols[norm]
        num_exist = as_numeric(existing)
        num_new = as_numeric(series)
        c_exist = num_exist.dropna().nunique()
        c_new = num_new.dropna().nunique()

        if c_new > c_exist:
            final_cols[norm] = series
        elif c_new == c_exist and c_new > 0:
            if series.notna().sum() > existing.notna().sum():
                final_cols[norm] = series
        elif existing.isna().all() and series.notna().any():
            final_cols[norm] = series

    cleaned = pd.DataFrame(final_cols)
    # Ensure unique columns and drop duplicate rows
    cleaned = cleaned.loc[:, ~cleaned.columns.duplicated()]
    cleaned.drop_duplicates(inplace=True)
    return cleaned


_XPATH_SCT_HEADER_TR = r"""
//tr[
  .//text()[contains(translate(., 'ABCDEFGHIJKLMNOPQRSTUVWXYZ', 'abcdefghijklmnopqrstuvwxyz'), 'name')]
  and (
    (
      .//text()[contains(translate(., 'ABCDEFGHIJKLMNOPQRSTUVWXYZ', 'abcdefghijklmnopqrstuvwxyz'), 'principal')]
      and .//text()[contains(translate(., 'ABCDEFGHIJKLMNOPQRSTUVWXYZ', 'abcdefghijklmnopqrstuvwxyz'), 'position')]
    )
    or (
      following-sibling::tr[1]//text()[contains(translate(., 'ABCDEFGHIJKLMNOPQRSTUVWXYZ', 'abcdefghijklmnopqrstuvwxyz'), 'principal')]
      and following-sibling::tr[1]//text()[contains(translate(., 'ABCDEFGHIJKLMNOPQRSTUVWXYZ', 'abcdefghijklmnopqrstuvwxyz'), 'position')]
    )
  )
]
"""


def _unique_tables(tr_nodes) -> List:
    seen = set()
    out = []
    for tr in tr_nodes:
        table = tr.getparent()
        while table is not None and getattr(table, "tag", None) != "table":
            table = table.getparent()
        if table is None:
            continue
        key = LH.tostring(table)[:200]  # cheap content hash key
        if key in seen:
            continue
        seen.add(key)
        out.append(table)
    return out


def extract_sct_tables_from_bytes(html_bytes: bytes) -> List[pd.DataFrame]:
    """Return candidate SCT tables as cleaned DataFrames (may be empty list)."""
    try:
        tree = LH.fromstring(html_bytes)
    except Exception:
        return []
    tr_nodes = tree.xpath(_XPATH_SCT_HEADER_TR)
    if not tr_nodes:
        return []
    tables = _unique_tables(tr_nodes)
    dfs: List[pd.DataFrame] = []
    for t in tables:
        try:
            df = process_extracted_table(t)
            if not df.empty:
                dfs.append(df)
        except Exception:
            continue
    return dfs


def extract_sct_tables_from_file(path: str | Path) -> List[pd.DataFrame]:
    p = Path(path)
    try:
        html_bytes = p.read_bytes()
    except Exception:
        return []
    return extract_sct_tables_from_bytes(html_bytes)


# **Reading the Files**

###**Extracting CSV from the HTML Tables**

In [36]:
# @title
# import glob

# html_list = glob.glob('/content/*_SCT*.html')
# # html_list = glob.glob('/content/A_2013-02-06_SCT*.html')
# print(html_list)

Extracting the data from google drive

In [262]:
from google.colab import drive
drive.mount('/content/drive')

import glob
import pandas as pd

from google.colab import data_table
data_table.enable_dataframe_formatter()

base_path = "/content/drive/MyDrive/data/"

# recursive search through all ticker folders
html_list = glob.glob(base_path + "**/DEF_14A/extracted/*_SCT*.html", recursive=True)

print(f"FOUND {len(html_list)} SCT HTML FILES\n")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
FOUND 966 SCT HTML FILES



In [263]:
print(list(html_list)[:1])

['/content/drive/MyDrive/data/AZPN/DEF_14A/extracted/AZPN_2022-10-28_SCT_table2.html']


In [39]:
# @title
# html_tables = {}

# for path in html_list[:20]:
#     try:
#         ticker = path.split("/")[-4]   # extract ticker folder name
#         df_list = pd.read_html(path)
#         print(f"Extracted {len(df_list)} tables from {path}")
#         # print(df_list)
#         combined = pd.concat(df_list, ignore_index=True)
#         html_tables[(ticker, path)] = combined
#         print(f"Loaded: {ticker} → {path}")
#     except Exception as e:
#         print(f"FAILED: {path} → {e}")

# print("\nDONE.")

In [40]:
# @title
# # print(list(html_tables.items())[:1])
# print(list(html_tables.keys())[:1])

###Combine HTML to one dataframe

In [264]:
def combined_html_df(htmlfile):
    # extract tables
    tables = pd.read_html(htmlfile)
    combined = pd.concat(tables, ignore_index=True)

    return combined

In [265]:
# target_path = "/content/drive/MyDrive/data/AIRT/DEF_14A/extracted/AIRT_2009-07-15_SCT.html"

In [266]:
csv_tables = {}

for htmlfile in html_list[:20]:
  # if htmlfile == target_path:
    # print("Processing:", htmlfile)
    df_name = os.path.splitext(os.path.basename(htmlfile))[0]
    csv_tables[df_name] = combined_html_df(htmlfile)
    print(f"processed:", df_name)

processed: AZPN_2022-10-28_SCT_table2
processed: AZPN_2022-10-28_SCT_table3
processed: AZPN_2023-10-24_SCT
processed: AZPN_2024-10-24_SCT
processed: AZPN_2022-10-28_SCT_table1
processed: AIRT_2025-07-03_SCT
processed: AIRT_2023-07-24_SCT
processed: AIRT_2009-07-15_SCT
processed: AIRT_2005-08-12_SCT
processed: AIRT_2024-07-10_SCT
processed: AIRT_2015-07-22_SCT
processed: AIRT_2012-07-20_SCT
processed: AIRT_2008-08-14_SCT
processed: AIRT_2007-08-13_SCT
processed: AIRT_2013-07-22_SCT
processed: AIRT_2011-07-15_SCT
processed: AIRT_2021-07-19_SCT
processed: AIRT_2020-07-20_SCT
processed: AIRT_2014-07-18_SCT
processed: AIRT_2022-07-05_SCT


In [267]:
csv_dataframes = csv_tables.copy()
print(csv_dataframes.keys())

dict_keys(['AZPN_2022-10-28_SCT_table2', 'AZPN_2022-10-28_SCT_table3', 'AZPN_2023-10-24_SCT', 'AZPN_2024-10-24_SCT', 'AZPN_2022-10-28_SCT_table1', 'AIRT_2025-07-03_SCT', 'AIRT_2023-07-24_SCT', 'AIRT_2009-07-15_SCT', 'AIRT_2005-08-12_SCT', 'AIRT_2024-07-10_SCT', 'AIRT_2015-07-22_SCT', 'AIRT_2012-07-20_SCT', 'AIRT_2008-08-14_SCT', 'AIRT_2007-08-13_SCT', 'AIRT_2013-07-22_SCT', 'AIRT_2011-07-15_SCT', 'AIRT_2021-07-19_SCT', 'AIRT_2020-07-20_SCT', 'AIRT_2014-07-18_SCT', 'AIRT_2022-07-05_SCT'])


###Basic text cleaning

In [268]:
def clean_text_basic(raw: str) -> str:
    if raw is None:
        return ""

    s = str(raw)
    s = s.replace("\u00a0", " ")                     # non-breaking space
    s = re.sub(r"(\w)-\s+(\w)", r"\1\2", s)         # fix hyphen splits
    s = s.replace("/", " ")                         # slash spacing
    s = re.sub(r"\s+", " ", s).strip()              # collapse whitespace
    s = re.sub(r"\s*\([^)]*\)", "", s)              # footnotes
    s = s.replace("$", "")
    s = s.replace(",", "")
    s = re.sub(r"\s+", " ", s).strip().lower()

    if not s:
        return ""

    return s

def clean_basic_dataframe(df: pd.DataFrame) -> pd.DataFrame:
    df2 = df.copy()
    for col in df2.columns:
        df2[col] = df2[col].apply(
            lambda x: clean_text_basic(x) if isinstance(x, str) else x
        )
    return df2

In [269]:
for name, df in csv_dataframes.items():

    # 1️⃣ basic cleaning
    df = clean_basic_dataframe(df)

    # overwrite original entry
    csv_dataframes[name] = df

    print(f"✔ processed: {name}")

✔ processed: AZPN_2022-10-28_SCT_table2
✔ processed: AZPN_2022-10-28_SCT_table3
✔ processed: AZPN_2023-10-24_SCT
✔ processed: AZPN_2024-10-24_SCT
✔ processed: AZPN_2022-10-28_SCT_table1
✔ processed: AIRT_2025-07-03_SCT
✔ processed: AIRT_2023-07-24_SCT
✔ processed: AIRT_2009-07-15_SCT
✔ processed: AIRT_2005-08-12_SCT
✔ processed: AIRT_2024-07-10_SCT
✔ processed: AIRT_2015-07-22_SCT
✔ processed: AIRT_2012-07-20_SCT
✔ processed: AIRT_2008-08-14_SCT
✔ processed: AIRT_2007-08-13_SCT
✔ processed: AIRT_2013-07-22_SCT
✔ processed: AIRT_2011-07-15_SCT
✔ processed: AIRT_2021-07-19_SCT
✔ processed: AIRT_2020-07-20_SCT
✔ processed: AIRT_2014-07-18_SCT
✔ processed: AIRT_2022-07-05_SCT


###Reading CSV

In [196]:
# files = os.listdir('/content')
# # print(files)
# csv_list = []

# for f in files:
#   if f.endswith('.csv'):
#     csv_list.append(f)

# print(csv_list)

In [197]:
# # import pandas as pd
# # import os

# # Get a list of all .csv files in the current directory
# csv_files = [f for f in os.listdir('/content') if f.endswith('.csv')]

# # Dictionary to store DataFrames
# csv_dataframes = {}

# # Read each CSV file into a pandas DataFrame and store it in the dictionary
# for file in csv_files:
#     file_path = os.path.join('/content', file)
#     df_name = os.path.splitext(file)[0] # Get filename without extension
#     csv_dataframes[df_name] = pd.read_csv(file_path)
#     print(f"Successfully loaded '{file}' into DataFrame '{df_name}'")

### Displaying the first 5 rows of each loaded DataFrame:

In [272]:
for df_name, df in csv_dataframes.items():
    print(f"\n--- DataFrame: {df_name} ---")
    # df = df.replace({$}as())) # This line caused a SyntaxError and has been commented out
    display(df)


--- DataFrame: AZPN_2022-10-28_SCT_table2 ---


0   \
0                                                 NaN   
1                          summary compensation table   
2                         name and principal position   
3                                                 NaN   
4                                   antonio j. pietri   
5                                       president and   
6                             chief executive officer   
7                                                 NaN   
8                                                 NaN   
9                                chantelle breithaupt   
10                          senior vice president and   
11                            chief financial officer   
12                                                NaN   
13                                      manish chawla   
14  executive vice president and chief revenue off...   
15                                                NaN   
16                                frederic g. hammond   
17  senior vice president general counsel and secr...   
18                                                NaN   
19                                                NaN   
20                                                NaN   
21  amounts shown represent aggregate grant date f...   
22                                                NaN   
23  prior to the closing of the emerson transactio...   
24                                                NaN   
25  amounts shown include matching contributions u...   
26                                                NaN   
27  mr. chawla was appointed as our executive vice...   

                                                   1   \
0                                                 NaN   
1                          summary compensation table   
2                         name and principal position   
3                                                 NaN   
4                                   antonio j. pietri   
5                                       president and   
6                             chief executive officer   
7                                                 NaN   
8                                                 NaN   
9                                chantelle breithaupt   
10                          senior vice president and   
11                            chief financial officer   
12                                                NaN   
13                                      manish chawla   
14  executive vice president and chief revenue off...   
15                                                NaN   
16                                frederic g. hammond   
17  senior vice president general counsel and secr...   
18                                                NaN   
19                                                NaN   
20                                                NaN   
21  amounts shown represent aggregate grant date f...   
22                                                NaN   
23  prior to the closing of the emerson transactio...   
24                                                NaN   
25  amounts shown include matching contributions u...   
26                                                NaN   
27  mr. chawla was appointed as our executive vice...   

                                                   2   \
0                                                 NaN   
1                          summary compensation table   
2                         name and principal position   
3                                                 NaN   
4                                   antonio j. pietri   
5                                       president and   
6                             chief executive officer   
7                                                 NaN   
8                                                 NaN   
9                                chantelle breithaupt   
10                          senior vice president and   
11                            chief financial officer   
12


--- DataFrame: AZPN_2022-10-28_SCT_table3 ---


0   \
0                                                 NaN   
1                                                 NaN   
2                          summary compensation table   
3                          summary compensation table   
4                         name and principal position   
5                                                 NaN   
6                                   antonio j. pietri   
7                                       president and   
8                             chief executive officer   
9                                                 NaN   
10                               chantelle breithaupt   
11                              senior vice president   
12                        and chief financial officer   
13                                                NaN   
14                                      manish chawla   
15                           executive vice president   
16                          and chief revenue officer   
17                                                NaN   
18                                frederic g. hammond   
19                              senior vice president   
20                      general counsel and secretary   
21                                                NaN   
22                                                NaN   
23  amounts shown represent aggregate grant date f...   
24  amounts shown represent aggregate grant date f...   
25  amounts shown represent aggregate grant date f...   
26  amounts shown represent aggregate grant date f...   
27                                                NaN   
28  amounts shown consist of awards based on perfo...   
29  amounts shown consist of awards based on perfo...   
30                                                NaN   
31  amounts shown include matching contributions u...   
32  amounts shown include matching contributions u...   
33                                                NaN   
34  mr. chawla was appointed as our executive vice...   
35                                                NaN   

                                                   1   \
0                                                 NaN   
1                                                 NaN   
2                          summary compensation table   
3                          summary compensation table   
4                         name and principal position   
5                                                 NaN   
6                                   antonio j. pietri   
7                                       president and   
8                             chief executive officer   
9                                                 NaN   
10                               chantelle breithaupt   
11                              senior vice president   
12                        and chief financial officer   
13                                                NaN   
14                                      manish chawla   
15                           executive vice president   
16                          and chief revenue officer   
17                                                NaN   
18                                frederic g. hammond   
19                              senior vice president   
20                      general counsel and secretary   
21                                                NaN   
22                                                NaN   
23  amounts shown represent aggregate grant date f...   
24  amounts shown represent aggregate grant date f...   
25  amounts shown represent aggregate grant date f...   
26  amounts shown represent aggregate grant date f...   
27                                                NaN   
28  amounts shown consist of awards based on perfo...   
29  amounts shown consist of awards based on perfo...   
30                                                NaN   
31  amounts shown include matching contributions u...   
32  amounts shown include matching contributions u...   
33 


--- DataFrame: AZPN_2023-10-24_SCT ---


...

0   \
0                                                NaN   
1                        name and principal position   
2                                                NaN   
3           nicholas swenson chief executive officer   
4           nicholas swenson chief executive officer   
5                                                NaN   
6              brian ochocki chief financial officer   
7              brian ochocki chief financial officer   
8                                                NaN   
9   brett a. reynolds former chief financial officer   
10  brett a. reynolds former chief financial officer   
11                                               NaN   

                                                  1   \
0                                                NaN   
1                        name and principal position   
2                                                NaN   
3           nicholas swenson chief executive officer   
4           nicholas swenson chief executive officer   
5                                                NaN   
6              brian ochocki chief financial officer   
7              brian ochocki chief financial officer   
8                                                NaN   
9   brett a. reynolds former chief financial officer   
10  brett a. reynolds former chief financial officer   
11                                               NaN   

                                                  2     3     4     5   \
0                                                NaN   NaN   NaN   NaN   
1                        name and principal position  year  year  year   
2                                                NaN   NaN   NaN   NaN   
3           nicholas swenson chief executive officer  2020  2020  2020   
4           nicholas swenson chief executive officer  2019  2019  2019   
5                                                NaN   NaN   NaN   NaN   
6              brian ochocki chief financial officer  2020  2020  2020   
7              brian ochocki chief financial officer  2019  2019  2019   
8                                                NaN   NaN   NaN   NaN   
9   brett a. reynolds former chief financial officer  2020  2020  2020   
10  brett a. reynolds former chief financial officer  2019  2019  2019   
11                                               NaN   NaN   NaN   NaN   

        6       7       8      9   ...  \
0      NaN     NaN     NaN    NaN  ...   
1   salary  salary  salary  bonus  ...   
2      NaN     NaN     NaN    NaN  ...   
3    50000   50000   50000    250  ...   
4    50000   50000   50000      0  ...   
5      NaN     NaN     NaN    NaN  ...   
6   161000  161000  161000    250  ...   
7       --      --      --     --  ...   
8      NaN     NaN     NaN    NaN  ...   
9    10000   10000   10000      0  ...   
10  265000  265000  265000    150  ...   
11     NaN     NaN     NaN    NaN  ...   

                                        14  \
0                                      NaN   
1   non-equity incentive plan compensation   
2                                      NaN   
3                                        0   
4                                        0   
5                                      NaN   
6                                        0   
7                                       --   
8                                      NaN   
9                                        0   
10                                       0   
11                                     NaN   

                                                   15  \
0                                                 NaN   
1   change in pension value and non-qualified defe...   
2                                                 NaN   
3                                                   0   
4                                                   0   
5                                                 NaN   
6                                                   0   
7                          


--- DataFrame: AIRT_2014-07-18_SCT ---


0   1     2     3   4   5   \
0                                                NaN NaN   NaN   NaN NaN NaN   
1                        name and principal position NaN  year  year NaN NaN   
2  nicholas j. swenson interim chief executive of... NaN   NaN  2014 NaN NaN   
3                                         john parry NaN   NaN  2014 NaN NaN   
4  former vice president-finance chief financial ... NaN   NaN  2013 NaN NaN   
5                                 william h. simpson NaN   NaN  2014 NaN NaN   
6              executive vice president and director NaN   NaN  2013 NaN NaN   
7                                       walter clark NaN   NaN  2014 NaN NaN   
8        former chief executive officer and director NaN   NaN  2013 NaN NaN   

       6       7   8   9   ...  \
0     NaN     NaN NaN NaN  ...   
1  salary  salary NaN NaN  ...   
2     NaN       — NaN NaN  ...   
3     NaN  187200 NaN NaN  ...   
4     NaN  179200 NaN NaN  ...   
5     NaN  254600 NaN NaN  ...   
6     NaN  249700 NaN NaN  ...   
7     NaN  181900 NaN NaN  ...   
8     NaN  256000 NaN NaN  ...   

                                                  19  20  21  \
0                                                NaN NaN NaN   
1  change in pension value and nonqualified defer... NaN NaN   
2                                                  — NaN NaN   
3                                                  — NaN NaN   
4                                                  — NaN NaN   
5                                                  — NaN NaN   
6                                                  — NaN NaN   
7                                                  — NaN NaN   
8                                                  — NaN NaN   

                       22                      23   24  25     26      27  28  
0                     NaN                     NaN  NaN NaN    NaN     NaN NaN  
1  all other compensation  all other compensation  NaN NaN  total   total NaN  
2                     NaN                   17000      NaN    NaN   17000 NaN  
3                     NaN                   17448      NaN    NaN  251998 NaN  
4                     NaN                   15690  NaN NaN    NaN  241613 NaN  
5                     NaN                   17987      NaN    NaN  335720 NaN  
6                     NaN                   19469  NaN NaN    NaN  331466 NaN  
7                     NaN                  592709      NaN    NaN  810730 NaN  
8                     NaN                   25591  NaN NaN    NaN  343888 NaN  

[9 rows x 29 columns]


--- DataFrame: AIRT_2022-07-05_SCT ---


0   \
0                                       NaN   
1               name and principal position   
2                                       NaN   
3                                       NaN   
4  nicholas swenson chief executive officer   
5  nicholas swenson chief executive officer   
6                                       NaN   
7     brian ochocki chief financial officer   
8     brian ochocki chief financial officer   

                                         1   \
0                                       NaN   
1               name and principal position   
2                                       NaN   
3                                       NaN   
4  nicholas swenson chief executive officer   
5  nicholas swenson chief executive officer   
6                                       NaN   
7     brian ochocki chief financial officer   
8     brian ochocki chief financial officer   

                                         2     3     4     5       6       7   \
0                                       NaN   NaN   NaN   NaN     NaN     NaN   
1               name and principal position  year  year  year  salary  salary   
2                                       NaN   NaN   NaN   NaN     NaN     NaN   
3                                       NaN   NaN   NaN   NaN     NaN     NaN   
4  nicholas swenson chief executive officer  2022  2022  2022   50000   50000   
5  nicholas swenson chief executive officer  2021  2021  2021   50000   50000   
6                                       NaN   NaN   NaN   NaN     NaN     NaN   
7     brian ochocki chief financial officer  2022  2022  2022  248000  248000   
8     brian ochocki chief financial officer  2021  2021  2021  231000  231000   

       8       9   ...                   17  \
0     NaN     NaN  ...                  NaN   
1  salary   bonus  ...  equity compensation   
2     NaN     NaN  ...        option awards   
3     NaN     NaN  ...                  NaN   
4   50000       0  ...               781595   
5   50000     250  ...                    0   
6     NaN     NaN  ...                  NaN   
7  248000  105500  ...                97699   
8  231000   20250  ...                    0   

                                       18  \
0                                     NaN   
1  non-equity incentive plan compensation   
2                                     NaN   
3                                     NaN   
4                                       0   
5                                       0   
6                                     NaN   
7                                       0   
8                                       0   

                                       19  \
0                                     NaN   
1  non-equity incentive plan compensation   
2                                     NaN   
3                                     NaN   
4                                       0   
5                                       0   
6                                     NaN   
7                                       0   
8                                       0   

                                       20                      21  \
0                                     NaN                     NaN   
1  non-equity incentive plan compensation  all other compensation   
2                                     NaN                     NaN   
3                                     NaN                     NaN   
4                                       0                       0   
5                                       0                       0   
6                                     NaN                     NaN   
7                                       0                       0   
8                                       0                       0   

                       22                      23      24      25      26  
0                     NaN                     NaN     NaN     NaN     NaN  
1  all other compensation  all other compensation   total   total   tota

###Detect Headers

In [252]:
from typing import List, Dict, Tuple, Optional

# 3) Detect header row
CANON_ORDER = [
    'executive_name','position','year',
    'salary','bonus','stock_awards','option_awards',
    'non_equity_incentive','pension_value','all_other_comp','total',
]
KEY_TOKENS: Dict[str, List[str]] = {
    'salary': ['salary'],
    'bonus': ['bonus'],
    'stock_awards': ['stock awards','stock-awards'],
    'option_awards': ['option awards','option-awards'],
    'non_equity_incentive': ['non-equity incentive','non equity incentive'],
    'pension_value': ['change in pension','pension value','deferred compensation earnings'],
    'all_other_comp': ['all other compensation'],
    'total': ['total'],
    'year': ['year','fiscal year'],
    'name_position': ['name and principal position','name & principal position','principal position','name'],
}
PLACEHOLDER_HEADERS = {'','$','—','–','-'}

def detect_header_row(df: pd.DataFrame, max_rows: int = 6) -> pd.DataFrame:
    for i in range(min(max_rows, len(df))):
        row_low = df.iloc[i].astype(str).str.lower()
        joined = ' '.join(list(row_low))
        hits = 0
        for toks in KEY_TOKENS.values():
            if any(tok in joined for tok in toks):
                hits += 1
        if hits >= 2:
            df2 = df.copy()
            df2.columns = df2.iloc[i].astype(str).tolist()
            df2 = df2.iloc[i+1:].reset_index(drop=True)
            return df2
    return df


In [253]:
for df_name, df in csv_dataframes.items():
    csv_dataframes[df_name] = detect_header_row(df)
    print(f"Processed: {df_name}")

Processed: AZPN_2022-10-28_SCT_table2
Processed: AZPN_2022-10-28_SCT_table3
Processed: AZPN_2023-10-24_SCT
Processed: AZPN_2024-10-24_SCT
Processed: AZPN_2022-10-28_SCT_table1
Processed: AIRT_2025-07-03_SCT
Processed: AIRT_2023-07-24_SCT
Processed: AIRT_2009-07-15_SCT
Processed: AIRT_2005-08-12_SCT
Processed: AIRT_2024-07-10_SCT
Processed: AIRT_2015-07-22_SCT
Processed: AIRT_2012-07-20_SCT
Processed: AIRT_2008-08-14_SCT
Processed: AIRT_2007-08-13_SCT
Processed: AIRT_2013-07-22_SCT
Processed: AIRT_2011-07-15_SCT
Processed: AIRT_2021-07-19_SCT
Processed: AIRT_2020-07-20_SCT
Processed: AIRT_2014-07-18_SCT
Processed: AIRT_2022-07-05_SCT


### Displaying the first 5 rows of each loaded DataFrame:

In [201]:
for df_name, df in csv_dataframes.items():
    print(f"\n--- DataFrame: {df_name} ---")
    # df = df.replace({$}as())) # This line caused a SyntaxError and has been commented out
    df.shape
    display(df.head())


--- DataFrame: AZPN_2022-10-28_SCT_table2 ---


name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position  year  year  year  salary  salary  salary  \
0                         NaN   NaN   NaN   NaN     NaN     NaN     NaN   
1           antonio j. pietri  2022  2022  2022  468750  468750  468750   
2               president and  2021  2021  2021  600000  600000  600000   
3     chief executive officer  2020  2020  2020  600000  600000  600000   
4                         NaN  2019  2019  2019  586186  586186  586186   

  stock awards  ... non-equity incentive plan compensation  \
0          NaN  ...                                    NaN   
1      7800162  ...                                 600000   
2      4649941  ...                                 320000   
3           --  ...                                 713920   
4      4650012  ...                                 721990   

  all other compensation all other compensation all other compensation  \
0                    NaN                    NaN                    NaN   
1                   7175                   7175                   7175   
2                   9273                   9273                   9273   
3                   8211                   8211                   8211   
4                   8967                   8967                   8967   

      total     total     total  nan  nan  nan  
0       NaN       NaN       NaN  NaN  NaN  NaN  
1  14942013  14942013  14942013  NaN  NaN  NaN  
2   8418919   8418919   8418919  NaN  NaN  NaN  
3   1322131   1322131   1322131  NaN  NaN  NaN  
4   7621337   7621337   7621337  NaN  NaN  NaN  

[5 rows x 27 columns]


--- DataFrame: AZPN_2022-10-28_SCT_table3 ---


name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position  year  ... all other compensation     total  \
0                         NaN   NaN  ...                    NaN       NaN   
1           antonio j. pietri  2022  ...                   9567  22635094   
2               president and  2021  ...                   9273   8418919   
3     chief executive officer  2020  ...                   8211   7626325   
4                         NaN   NaN  ...                    NaN       NaN   

      total     total     total     total     total     total     total  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1  22635094  22635094  22635094  22635094  22635094  22635094  22635094   
2   8418919   8418919   8418919   8418919   8418919   8418919   8418919   
3   7626325   7626325   7626325   7626325   7626325   7626325   7626325   
4       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

      total  
0       NaN  
1  22635094  
2   8418919  
3   7626325  
4       NaN  

[5 rows x 72 columns]


--- DataFrame: AZPN_2023-10-24_SCT ---


...

name and principal position  \
0                                       NaN   
1  nicholas swenson chief executive officer   
2  nicholas swenson chief executive officer   
3                                       NaN   
4     brian ochocki chief financial officer   

                name and principal position  \
0                                       NaN   
1  nicholas swenson chief executive officer   
2  nicholas swenson chief executive officer   
3                                       NaN   
4     brian ochocki chief financial officer   

                name and principal position  year  year  year  salary  salary  \
0                                       NaN   NaN   NaN   NaN     NaN     NaN   
1  nicholas swenson chief executive officer  2020  2020  2020   50000   50000   
2  nicholas swenson chief executive officer  2019  2019  2019   50000   50000   
3                                       NaN   NaN   NaN   NaN     NaN     NaN   
4     brian ochocki chief financial officer  2020  2020  2020  161000  161000   

   salary bonus  ... non-equity incentive plan compensation  \
0     NaN   NaN  ...                                    NaN   
1   50000   250  ...                                      0   
2   50000     0  ...                                      0   
3     NaN   NaN  ...                                    NaN   
4  161000   250  ...                                      0   

  change in pension value and non-qualified deferred compensation earnings  \
0                                                NaN                         
1                                                  0                         
2                                                  0                         
3                                                NaN                         
4                                                  0                         

  change in pension value and non-qualified deferred compensation earnings  \
0                                                NaN                         
1                                                  0                         
2                                                  0                         
3                                                NaN                         
4                                                  0                         

  change in pension value and non-qualified deferred compensation earnings  \
0                                                NaN                         
1                                                  0                         
2                                                  0                         
3                                                NaN                         
4                                                  0                         

  all other compensation all other compensation all other compensation  \
0                    NaN                    NaN                    NaN   
1                      0                      0                      0   
2                      0                      0                      0   
3                    NaN                    NaN                    NaN   
4                      0                      0                      0   

    total   total   total  
0     NaN     NaN     NaN  
1   50250   50250   50250  
2   50000   50000   50000  
3     NaN     NaN     NaN  
4  161250  161250  161250  

[5 rows x 24 columns]


--- DataFrame: AIRT_2014-07-18_SCT ---


name and principal position nan year  year nan nan  \
0  nicholas j. swenson interim chief executive of... NaN  NaN  2014 NaN NaN   
1                                         john parry NaN  NaN  2014 NaN NaN   
2  former vice president-finance chief financial ... NaN  NaN  2013 NaN NaN   
3                                 william h. simpson NaN  NaN  2014 NaN NaN   
4              executive vice president and director NaN  NaN  2013 NaN NaN   

  salary  salary nan nan  ...  \
0    NaN       — NaN NaN  ...   
1    NaN  187200 NaN NaN  ...   
2    NaN  179200 NaN NaN  ...   
3    NaN  254600 NaN NaN  ...   
4    NaN  249700 NaN NaN  ...   

  change in pension value and nonqualified deferred compensation earnings nan  \
0                                                  —                      NaN   
1                                                  —                      NaN   
2                                                  —                      NaN   
3                                                  —                      NaN   
4                                                  —                      NaN   

  nan all other compensation all other compensation  nan nan total   total nan  
0 NaN                    NaN                  17000      NaN   NaN   17000 NaN  
1 NaN                    NaN                  17448      NaN   NaN  251998 NaN  
2 NaN                    NaN                  15690  NaN NaN   NaN  241613 NaN  
3 NaN                    NaN                  17987      NaN   NaN  335720 NaN  
4 NaN                    NaN                  19469  NaN NaN   NaN  331466 NaN  

[5 rows x 29 columns]


--- DataFrame: AIRT_2022-07-05_SCT ---


name and principal position  \
0                                       NaN   
1                                       NaN   
2  nicholas swenson chief executive officer   
3  nicholas swenson chief executive officer   
4                                       NaN   

                name and principal position  \
0                                       NaN   
1                                       NaN   
2  nicholas swenson chief executive officer   
3  nicholas swenson chief executive officer   
4                                       NaN   

                name and principal position  year  year  year salary salary  \
0                                       NaN   NaN   NaN   NaN    NaN    NaN   
1                                       NaN   NaN   NaN   NaN    NaN    NaN   
2  nicholas swenson chief executive officer  2022  2022  2022  50000  50000   
3  nicholas swenson chief executive officer  2021  2021  2021  50000  50000   
4                                       NaN   NaN   NaN   NaN    NaN    NaN   

  salary bonus  ... equity compensation  \
0    NaN   NaN  ...       option awards   
1    NaN   NaN  ...                 NaN   
2  50000     0  ...              781595   
3  50000   250  ...                   0   
4    NaN   NaN  ...                 NaN   

  non-equity incentive plan compensation  \
0                                    NaN   
1                                    NaN   
2                                      0   
3                                      0   
4                                    NaN   

  non-equity incentive plan compensation  \
0                                    NaN   
1                                    NaN   
2                                      0   
3                                      0   
4                                    NaN   

  non-equity incentive plan compensation all other compensation  \
0                                    NaN                    NaN   
1                                    NaN                    NaN   
2                                      0                      0   
3                                      0                      0   
4                                    NaN                    NaN   

  all other compensation all other compensation   total   total   total  
0                    NaN                    NaN     NaN     NaN     NaN  
1                    NaN                    NaN     NaN     NaN     NaN  
2                      0                      0  831595  831595  831595  
3                      0                      0   50250   50250   50250  
4                    NaN                    NaN     NaN     NaN     NaN  

[5 rows x 27 columns]

###Flatten the headers

In [254]:
# @title
# def flatten_headers(df: pd.DataFrame) -> pd.DataFrame:

#     # flatten multi-row headers into one line
#     df = _flatten_columns(df)
#     # strip whitespace in all cells
#     combined = _strip_cells(combined)

#     combined = combined.loc[:, ~combined.columns.duplicated()]
#     # drop empty rows/cols early
#     combined = combined.dropna(axis=0, how='all')
#     combined = combined.dropna(axis=1, how='all')

In [255]:
for df_name, df in csv_dataframes.items():
    csv_dataframes[df_name] = _flatten_columns(df)
    # csv_dataframes[df_name] = _strip_cells(csv_dataframes[df_name])

###Independent Drop NA

In [244]:
for df_name, df in csv_dataframes.items():
    csv_dataframes[df_name] = df.dropna(axis=0, how='all')
    csv_dataframes[df_name] = df.dropna(axis=1, how='all')

### Displaying the first 5 rows of each loaded DataFrame:

In [256]:
for df_name, df in csv_dataframes.items():
    print(f"\n--- DataFrame: {df_name} ---")
    # df = df.replace({$}as())) # This line caused a SyntaxError and has been commented out
    df.shape
    display(df.head())


--- DataFrame: AZPN_2022-10-28_SCT_table2 ---


name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position  year  year  year  salary  salary  salary  \
0                         NaN   NaN   NaN   NaN     NaN     NaN     NaN   
1           antonio j. pietri  2022  2022  2022  468750  468750  468750   
2               president and  2021  2021  2021  600000  600000  600000   
3     chief executive officer  2020  2020  2020  600000  600000  600000   
4                         NaN  2019  2019  2019  586186  586186  586186   

  stock awards  ... non-equity incentive plan compensation  \
0          NaN  ...                                    NaN   
1      7800162  ...                                 600000   
2      4649941  ...                                 320000   
3           --  ...                                 713920   
4      4650012  ...                                 721990   

  all other compensation all other compensation all other compensation  \
0                    NaN                    NaN                    NaN   
1                   7175                   7175                   7175   
2                   9273                   9273                   9273   
3                   8211                   8211                   8211   
4                   8967                   8967                   8967   

      total     total     total  nan  nan  nan  
0       NaN       NaN       NaN  NaN  NaN  NaN  
1  14942013  14942013  14942013  NaN  NaN  NaN  
2   8418919   8418919   8418919  NaN  NaN  NaN  
3   1322131   1322131   1322131  NaN  NaN  NaN  
4   7621337   7621337   7621337  NaN  NaN  NaN  

[5 rows x 27 columns]


--- DataFrame: AZPN_2022-10-28_SCT_table3 ---


name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position name and principal position  \
0                         NaN                         NaN   
1           antonio j. pietri           antonio j. pietri   
2               president and               president and   
3     chief executive officer     chief executive officer   
4                         NaN                         NaN   

  name and principal position  year  ... all other compensation     total  \
0                         NaN   NaN  ...                    NaN       NaN   
1           antonio j. pietri  2022  ...                   9567  22635094   
2               president and  2021  ...                   9273   8418919   
3     chief executive officer  2020  ...                   8211   7626325   
4                         NaN   NaN  ...                    NaN       NaN   

      total     total     total     total     total     total     total  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1  22635094  22635094  22635094  22635094  22635094  22635094  22635094   
2   8418919   8418919   8418919   8418919   8418919   8418919   8418919   
3   7626325   7626325   7626325   7626325   7626325   7626325   7626325   
4       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

      total  
0       NaN  
1  22635094  
2   8418919  
3   7626325  
4       NaN  

[5 rows x 72 columns]


--- DataFrame: AZPN_2023-10-24_SCT ---


...

name and principal position  \
0                                       NaN   
1  nicholas swenson chief executive officer   
2  nicholas swenson chief executive officer   
3                                       NaN   
4     brian ochocki chief financial officer   

                name and principal position  \
0                                       NaN   
1  nicholas swenson chief executive officer   
2  nicholas swenson chief executive officer   
3                                       NaN   
4     brian ochocki chief financial officer   

                name and principal position  year  year  year  salary  salary  \
0                                       NaN   NaN   NaN   NaN     NaN     NaN   
1  nicholas swenson chief executive officer  2020  2020  2020   50000   50000   
2  nicholas swenson chief executive officer  2019  2019  2019   50000   50000   
3                                       NaN   NaN   NaN   NaN     NaN     NaN   
4     brian ochocki chief financial officer  2020  2020  2020  161000  161000   

   salary bonus  ... non-equity incentive plan compensation  \
0     NaN   NaN  ...                                    NaN   
1   50000   250  ...                                      0   
2   50000     0  ...                                      0   
3     NaN   NaN  ...                                    NaN   
4  161000   250  ...                                      0   

  change in pension value and non-qualified deferred compensation earnings  \
0                                                NaN                         
1                                                  0                         
2                                                  0                         
3                                                NaN                         
4                                                  0                         

  change in pension value and non-qualified deferred compensation earnings  \
0                                                NaN                         
1                                                  0                         
2                                                  0                         
3                                                NaN                         
4                                                  0                         

  change in pension value and non-qualified deferred compensation earnings  \
0                                                NaN                         
1                                                  0                         
2                                                  0                         
3                                                NaN                         
4                                                  0                         

  all other compensation all other compensation all other compensation  \
0                    NaN                    NaN                    NaN   
1                      0                      0                      0   
2                      0                      0                      0   
3                    NaN                    NaN                    NaN   
4                      0                      0                      0   

    total   total   total  
0     NaN     NaN     NaN  
1   50250   50250   50250  
2   50000   50000   50000  
3     NaN     NaN     NaN  
4  161250  161250  161250  

[5 rows x 24 columns]


--- DataFrame: AIRT_2014-07-18_SCT ---


name and principal position nan year  year nan nan  \
0  nicholas j. swenson interim chief executive of... NaN  NaN  2014 NaN NaN   
1                                         john parry NaN  NaN  2014 NaN NaN   
2  former vice president-finance chief financial ... NaN  NaN  2013 NaN NaN   
3                                 william h. simpson NaN  NaN  2014 NaN NaN   
4              executive vice president and director NaN  NaN  2013 NaN NaN   

  salary  salary nan nan  ...  \
0    NaN       — NaN NaN  ...   
1    NaN  187200 NaN NaN  ...   
2    NaN  179200 NaN NaN  ...   
3    NaN  254600 NaN NaN  ...   
4    NaN  249700 NaN NaN  ...   

  change in pension value and nonqualified deferred compensation earnings nan  \
0                                                  —                      NaN   
1                                                  —                      NaN   
2                                                  —                      NaN   
3                                                  —                      NaN   
4                                                  —                      NaN   

  nan all other compensation all other compensation  nan nan total   total nan  
0 NaN                    NaN                  17000      NaN   NaN   17000 NaN  
1 NaN                    NaN                  17448      NaN   NaN  251998 NaN  
2 NaN                    NaN                  15690  NaN NaN   NaN  241613 NaN  
3 NaN                    NaN                  17987      NaN   NaN  335720 NaN  
4 NaN                    NaN                  19469  NaN NaN   NaN  331466 NaN  

[5 rows x 29 columns]


--- DataFrame: AIRT_2022-07-05_SCT ---


name and principal position  \
0                                       NaN   
1                                       NaN   
2  nicholas swenson chief executive officer   
3  nicholas swenson chief executive officer   
4                                       NaN   

                name and principal position  \
0                                       NaN   
1                                       NaN   
2  nicholas swenson chief executive officer   
3  nicholas swenson chief executive officer   
4                                       NaN   

                name and principal position  year  year  year salary salary  \
0                                       NaN   NaN   NaN   NaN    NaN    NaN   
1                                       NaN   NaN   NaN   NaN    NaN    NaN   
2  nicholas swenson chief executive officer  2022  2022  2022  50000  50000   
3  nicholas swenson chief executive officer  2021  2021  2021  50000  50000   
4                                       NaN   NaN   NaN   NaN    NaN    NaN   

  salary bonus  ... equity compensation  \
0    NaN   NaN  ...       option awards   
1    NaN   NaN  ...                 NaN   
2  50000     0  ...              781595   
3  50000   250  ...                   0   
4    NaN   NaN  ...                 NaN   

  non-equity incentive plan compensation  \
0                                    NaN   
1                                    NaN   
2                                      0   
3                                      0   
4                                    NaN   

  non-equity incentive plan compensation  \
0                                    NaN   
1                                    NaN   
2                                      0   
3                                      0   
4                                    NaN   

  non-equity incentive plan compensation all other compensation  \
0                                    NaN                    NaN   
1                                    NaN                    NaN   
2                                      0                      0   
3                                      0                      0   
4                                    NaN                    NaN   

  all other compensation all other compensation   total   total   total  
0                    NaN                    NaN     NaN     NaN     NaN  
1                    NaN                    NaN     NaN     NaN     NaN  
2                      0                      0  831595  831595  831595  
3                      0                      0   50250   50250   50250  
4                    NaN                    NaN     NaN     NaN     NaN  

[5 rows x 27 columns]

###Cleaning and Normalizing Headers

In [230]:
# 5) Normalize headers + drop placeholder columns (robust for duplicate names)
def normalize_header(h: str) -> str:
    s = re.sub(r'\s+', ' ', str(h)).strip()
    s = re.sub(r'\([^)]*\)', '', s)
    s = s.replace(' ', ' ')
    s = re.sub(r'\s+', ' ', s).strip().lower()
    return s

def is_placeholder_col(obj) -> bool:
    import pandas as pd
    if isinstance(obj, pd.DataFrame):
        return all(is_placeholder_col(obj[c]) for c in obj.columns)
    sr = obj
    vals = sr.dropna().astype(str).str.strip().str.replace(' ',' ', regex=False)
    if vals.empty:
        return True
    return vals.str.fullmatch(r'(\$)?|—|–|-').all()

from typing import Tuple
def normalize_headers_and_drop_placeholders(df: pd.DataFrame) -> Tuple[pd.DataFrame, List[str]]:
    df2 = df.dropna(how='all').reset_index(drop=True).copy()
    df2.columns = [normalize_header(c) for c in df2.columns]
    df2 = df2.loc[:, ~df2.columns.duplicated()]
    dropped: List[str] = []
    # for c in list(df2.columns):
    #     if c in PLACEHOLDER_HEADERS:
    #         dropped.append(c)
    #         continue
    #     if is_placeholder_col(df2[c]):
    #         dropped.append(c)
    df2 = df2.drop(columns=list(set(dropped)), errors='ignore')
    return df2, dropped

# df_norm, dropped_cols = normalize_headers_and_drop_placeholders(df_flat.copy())
# print('Dropped placeholder columns:', dropped_cols)
# print('After normalize+drop: num rows/cols =', df_norm.shape)
# print('Columns (first 20):', list(df_norm.columns)[:20])
# display(df_norm.head(8))


In [231]:
for df_name, df in csv_dataframes.items():
  csv_dataframes[df_name], dropped_columns = normalize_headers_and_drop_placeholders(df)
  print(df_name,"Dropped Columns:", dropped_columns)

AZPN_2022-10-28_SCT_table2 Dropped Columns: []
AZPN_2022-10-28_SCT_table3 Dropped Columns: []
AZPN_2023-10-24_SCT Dropped Columns: []
AZPN_2024-10-24_SCT Dropped Columns: []
AZPN_2022-10-28_SCT_table1 Dropped Columns: []
AIRT_2025-07-03_SCT Dropped Columns: []
AIRT_2023-07-24_SCT Dropped Columns: []
AIRT_2009-07-15_SCT Dropped Columns: []
AIRT_2005-08-12_SCT Dropped Columns: []
AIRT_2024-07-10_SCT Dropped Columns: []
AIRT_2015-07-22_SCT Dropped Columns: []
AIRT_2012-07-20_SCT Dropped Columns: []
AIRT_2008-08-14_SCT Dropped Columns: []
AIRT_2007-08-13_SCT Dropped Columns: []
AIRT_2013-07-22_SCT Dropped Columns: []
AIRT_2011-07-15_SCT Dropped Columns: []
AIRT_2021-07-19_SCT Dropped Columns: []
AIRT_2020-07-20_SCT Dropped Columns: []
AIRT_2014-07-18_SCT Dropped Columns: []
AIRT_2022-07-05_SCT Dropped Columns: []


### Displaying the first 5 rows of each loaded DataFrame:

In [232]:
for df_name, df in csv_dataframes.items():
    # display using vega dataset


    print(f"\n--- DataFrame: {df_name} ---")
    # df = df.replace({$}as())) # This line caused a SyntaxError and has been commented out
    display(df.head())


--- DataFrame: AZPN_2022-10-28_SCT_table2 ---


name and principal position  year  salary stock awards option awards  \
0           antonio j. pietri  2022  468750      7800162       6065925   
1               president and  2021  600000      4649941       2839705   
2     chief executive officer  2020  600000           --            --   
3                         NaN  2019  586186      4650012       1654182   
4        chantelle breithaupt  2022  318750       637545            --   

  non-equity incentive plan compensation all other compensation     total  nan  
0                                 600000                   7175  14942013  NaN  
1                                 320000                   9273   8418919  NaN  
2                                 713920                   8211   1322131  NaN  
3                                 721990                   8967   7621337  NaN  
4                                 225000                   7509   1188804  NaN


--- DataFrame: AZPN_2022-10-28_SCT_table3 ---


name and principal position  year  salary stock awards option awards  \
0           antonio j. pietri  2022  618750     12415316       8791461   
1               president and  2021  600000      4649941       2839705   
2     chief executive officer  2020  600000      4650012       1654182   
3        chantelle breithaupt  2022  425000      2165028        902086   
4       senior vice president  2021  117420      2027673        836038   

  non-equity incentive plan compensation all other compensation     total  
0                                 800000                   9567  22635094  
1                                 320000                   9273   8418919  
2                                 713920                   8211   7626325  
3                                 300000                  10012   3802126  
4                                  33205                   6120   3020456


--- DataFrame: AZPN_2023-10-24_SCT ---


...


--- DataFrame: AIRT_2014-07-18_SCT ---


name and principal position  nan year salary  \
0  nicholas j. swenson interim chief executive of...  NaN  NaN    NaN   
1                                         john parry  NaN  NaN    NaN   
2  former vice president-finance chief financial ...  NaN  NaN    NaN   
3                                 william h. simpson  NaN  NaN    NaN   
4              executive vice president and director  NaN  NaN    NaN   

  option awards non-equity incentive plan compensation  \
0           NaN                                    NaN   
1           NaN                                    NaN   
2           NaN                                    NaN   
3           NaN                                    NaN   
4           NaN                                    NaN   

  change in pension value and nonqualified deferred compensation earnings  \
0                                                NaN                        
1                                                NaN                        
2                                                NaN                        
3                                                NaN                        
4                                                NaN                        

  all other compensation total  
0                    NaN   NaN  
1                    NaN   NaN  
2                    NaN   NaN  
3                    NaN   NaN  
4                    NaN   NaN


--- DataFrame: AIRT_2022-07-05_SCT ---


name and principal position  year  salary   bonus  \
0                                       NaN   NaN     NaN     NaN   
1  nicholas swenson chief executive officer  2022   50000       0   
2  nicholas swenson chief executive officer  2021   50000     250   
3     brian ochocki chief financial officer  2022  248000  105500   
4     brian ochocki chief financial officer  2021  231000   20250   

  equity compensation non-equity incentive plan compensation  \
0        stock awards                                    NaN   
1                   0                                      0   
2                   0                                      0   
3                   0                                      0   
4                   0                                      0   

  all other compensation   total  
0                    NaN     NaN  
1                      0  831595  
2                      0   50250  
3                      0  451199  
4                      0  251250

Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.


###Clearing columns and remaiming n_a as 0

In [53]:
# import numpy as np
# for df_name, df in csv_dataframes_normalized.items():
#     df = df.replace("n_a", "0")

#     df = df.replace([""," "], np.nan)

#     # drop columns literally named 'nan' or empty string
#     # bad_cols = [c for c in df.columns if str(c).lower() in ("nan", "")]
#     # df = df.drop(columns=bad_cols, errors='ignore')

#     # drop completely empty cols/rows
#     df = df.dropna(axis=1, how='all')
#     df = df.dropna(axis=0, how='all')

#     # 🔴 IMPORTANT: write it back
#     csv_dataframes_normalized[df_name] = df
import numpy as np

# for df_name, df in csv_dataframes_normalized.items():
for df_name, df in csv_dataframes.items():

    # 1️⃣ convert placeholders to real values
    df = df.replace("n_a", np.nan)
    df = df.replace("0_0_0", "0")    # optional – handles triple zeros
    df = df.replace("-", np.nan)     # optional – SEC uses dash for NA

    # 2️⃣ convert blank strings to NaN
    df = df.replace(["", " "], np.nan)

    # 3️⃣ drop rows that are fully empty
    df = df.dropna(axis=0, how='all')

    # 4️⃣ drop columns that are fully empty
    df = df.dropna(axis=1, how='all')

    # 5️⃣ assign back
    # csv_dataframes_normalized[df_name] = df
    csv_dataframes[df_name] = df


    # print(f"Cleaned: {df_name} → {df.shape}")

/tmp/ipython-input-1947355312.py:28: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df = df.replace(["", " "], np.nan)
/tmp/ipython-input-1947355312.py:25: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df = df.replace("-", np.nan)     # optional – SEC uses dash for NA
/tmp/ipython-input-1947355312.py:28: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_o

In [54]:
# for df_name, df in csv_dataframes_normalized.items():
#     print(f"\n--- Headers for DataFrame: {df_name} ---")
#     print(df.columns.tolist())

In [55]:
# # for df_name, df in csv_dataframes_normalized.items():
# for df_name, df in csv_dataframes.items():

#     print(f"\n--- cleaned DataFrame: {df_name} ---")
#     display(df)

### Normalizaing the Headers

In [59]:
# @title
# import re
# import pandas as pd # Ensure pandas is imported if not already

# def normalize_sct_text(raw: str) -> str:
#     """Normalize any SCT-related text (headers or cells) to a stable key."""
#     if raw is None:
#         return ""

#     s = str(raw).replace("\u00a0", " ")
#     s = re.sub(r"(\w)-\s+(\w)", r"\1\2", s)
#     s = s.replace("/", " ")
#     s = re.sub(r"\s+", " ", s).strip()
#     if not s:
#         return ""

#     # Remove footnotes and currency markers.
#     s = re.sub(r"\s*\([^)]*\)", "", s)
#     s = s.replace("$", "")
#     s = s.replace(",", "")
#     s = re.sub(r"\s+", " ", s).strip().lower()

#     # Specific rules for common headers
#     if re.search(r"\bname\b|\bposition\b|name.*(and|_).*position|position.*(and|_).*name|principal.?position|name.?and", s):
#         return "name_position"
#     if "fiscal" in s or re.search(r"\byear\b", s):
#         return "fiscal_year"
#     if "salary" in s:
#         return "salary"
#     if "bonus" in s:
#         return "bonus"
#     if "other annual" in s:
#         return "other_annual_comp"
#     if "stock" in s and "award" in s:
#         return "stock_awards"
#     if "option" in s:
#         return "option_awards"
#     if "non-equity" in s or "non equity" in s or "incentive plan" in s:
#         return "non_equity_incentive"
#     if "pension" in s or "deferred compensation" in s:
#         return "pension_value"
#     if "all other" in s:
#         return "all_other_comp"
#     if "total" in s:
#         return "total"

#     # Fallback: snake_case for unknown text.
#     return re.sub(r"[^a-z0-9]+", "_", s).strip("_")

# def normalize_dataframe_text(df):
#     """Normalize headers + all string cells using normalize_sct_text()."""
#     temp_df = df.copy()
#     potential_header_row_index = -1

#     # First, find the row that contains 'name_position' as a cell value
#     # We need to normalize cell values to find this. Do this on a temporary copy.
#     temp_processed_cells_df = temp_df.apply(lambda col: col.map(lambda x: normalize_sct_text(x) if isinstance(x, str) else x))

#     for i, row in temp_processed_cells_df.iterrows():
#         if 'name_position' in row.values:
#             potential_header_row_index = i
#             break

#     if potential_header_row_index != -1:
#         # Use the identified row's original values (after normalization) as new columns
#         new_columns = [normalize_sct_text(col_val) for col_val in temp_df.iloc[potential_header_row_index]]
#         temp_df.columns = new_columns
#         # Drop rows before and including the new header row
#         temp_df = temp_df.iloc[potential_header_row_index + 1:].reset_index(drop=True)
#     else:
#         # If no 'name_position' in cells to define a header row, just normalize existing headers
#         temp_df.columns = [normalize_sct_text(c) for c in temp_df.columns]

#     # Now apply normalization to all remaining string cells in the DataFrame
#     # This includes the new header row (which became column names) and the data rows.
#     return temp_df.apply(lambda col: col.map(lambda x: normalize_sct_text(x) if isinstance(x, str) else x))

In [60]:
# @title
# import re
# import pandas as pd

# def normalize_sct_text(raw: str) -> str:
#     """Normalize any SCT-related text (headers or cells) to a stable key."""
#     if raw is None:
#         return ""

#     s = str(raw).replace("\u00a0", " ")
#     s = re.sub(r"(\w)-\s+(\w)", r"\1\2", s)
#     s = s.replace("/", " ")
#     s = re.sub(r"\s+", " ", s).strip()
#     if not s:
#         return ""

#     # Remove footnotes and currency markers.
#     s = re.sub(r"\s*\([^)]*\)", "", s)
#     s = s.replace("$", "")
#     s = s.replace(",", "")
#     s = re.sub(r"\s+", " ", s).strip().lower()

#     # Specific rules for common headers
#     if re.search(r"\bname\b|\bposition\b|principal.?position", s):
#         return "name_position"
#     if "fiscal" in s or "year" in s:
#         return "fiscal_year"
#     if "salary" in s:
#         return "salary"
#     if "bonus" in s:
#         return "bonus"
#     if "stock" in s and "award" in s:
#         return "stock_awards"
#     if "option" in s:
#         return "option_awards"
#     if "equity" in s or "incentive" in s:
#         return "non_equity_incentive"
#     if "pension" in s:
#         return "pension_value"
#     if "all other" in s:
#         return "all_other_comp"
#     if "total" in s:
#         return "total"

#     # Fallback
#     return re.sub(r"[^a-z0-9]+", "_", s).strip("_")


# def normalize_dataframe_text(df):
#     """Normalize multi-row SCT tables into a clean single-header table."""

#     # STEP 1 — remove empty rows/cols early
#     df = df.dropna(axis=0, how='all')
#     df = df.dropna(axis=1, how='all')

#     # STEP 2 — use first 3 rows to build header (works for 2006–2007)
#     header_block = df.iloc[:3]

#     # STEP 3 — turn into strings & fill blanks
#     header_block = header_block.astype(str).replace("nan", "").fillna("")

#     # STEP 4 — merge header rows horizontally
#     merged_headers = header_block.apply(
#         lambda col: " ".join(col.values).strip()
#     )

#     # STEP 5 — normalize merged headers
#     normalized_headers = [
#         normalize_sct_text(h) for h in merged_headers
#     ]

#     # STEP 6 — assign column names
#     df.columns = normalized_headers

#     # STEP 7 — remove header rows from data
#     df = df.iloc[3:].reset_index(drop=True)

#     # STEP 8 — normalize remaining string cells
#     df = df.apply(
#         lambda col: col.map(
#             lambda x: normalize_sct_text(x) if isinstance(x, str) else x
#         )
#     )

#     return df

In [61]:
# @title
# for df_name, df in csv_dataframes.items():
#     csv_dataframes[df_name] = normalize_dataframe_text(df)
#     print(f"\n--- Normalized DataFrame: {df_name} ---")
#     display(csv_dataframes[df_name].head())

In [62]:
def normalize_semantic_text(raw: str) -> str:
    if raw is None:
        return ""

    s = str(raw).lower().strip()

    # category detection
    if "name" in s and "position" in s:
        return "name_position"
    if "fiscal" in s or "year" in s:
        return "fiscal_year"
    if "salary" in s:
        return "salary"
    if "bonus" in s:
        return "bonus"
    if "other annual" in s:
        return "other_annual_comp"
    if "stock" in s and "award" in s:
        return "stock_awards"
    if "option" in s:
        return "option_awards"
    if "incentive" in s:
        return "non_equity_incentive"
    if "pension" in s:
        return "pension_value"
    if "all other" in s:
        return "all_other_comp"
    if "total" in s:
        return "total"

    # fallback snake_case
    s = re.sub(r"[^a-z0-9]+", "_", s)
    return s.strip("_")

def normalize_semantic_dataframe(df: pd.DataFrame) -> pd.DataFrame:
    df2 = df.copy()

    # normalize column names
    df2.columns = [normalize_semantic_text(c) for c in df2.columns]

    # normalize cell values
    for col in df2.columns:
        df2[col] = df2[col].apply(
            lambda x: normalize_semantic_text(x) if isinstance(x, str) else x
        )

    return df2

In [63]:
for name, df in csv_dataframes.items():

    # 2️⃣ semantic category normalization
    df = normalize_semantic_dataframe(df)

    # overwrite original entry
    csv_dataframes[name] = df

    print(f"✔ processed: {name}")

✔ processed: AZPN_2022-10-28_SCT_table2
✔ processed: AZPN_2022-10-28_SCT_table3
✔ processed: AZPN_2023-10-24_SCT
✔ processed: AZPN_2024-10-24_SCT
✔ processed: AZPN_2022-10-28_SCT_table1
✔ processed: AIRT_2025-07-03_SCT
✔ processed: AIRT_2023-07-24_SCT
✔ processed: AIRT_2009-07-15_SCT
✔ processed: AIRT_2005-08-12_SCT
✔ processed: AIRT_2024-07-10_SCT
✔ processed: AIRT_2015-07-22_SCT
✔ processed: AIRT_2012-07-20_SCT
✔ processed: AIRT_2008-08-14_SCT
✔ processed: AIRT_2007-08-13_SCT
✔ processed: AIRT_2013-07-22_SCT
✔ processed: AIRT_2011-07-15_SCT
✔ processed: AIRT_2021-07-19_SCT
✔ processed: AIRT_2020-07-20_SCT
✔ processed: AIRT_2014-07-18_SCT
✔ processed: AIRT_2022-07-05_SCT


In [64]:
normalized_headers_after_text_normalization = set()

for df_name, df in csv_dataframes.items():
    normalized_headers_after_text_normalization.update(df.columns.tolist())

print("\n--- Summary of New Normalized Column Headers after Text Normalization ---")
print(sorted(list(normalized_headers_after_text_normalization)))


--- Summary of New Normalized Column Headers after Text Normalization ---
['', '1', '2', 'all_other_comp', 'all_other_compensation', 'bonus', 'equity_compensation', 'fiscal_year', 'name_position', 'nan', 'non_equity_incentive', 'nonqualified_deferred_compensation_earnings_4', 'option_awards', 'pension_value', 'salary', 'stock_awards', 'total']


In [65]:
# found = False

# for df_name, df in csv_dataframes.items():
#   if "name_position" in df.columns:
#     found = True
#     print(f"DataFrame '{df_name}' contains the 'name_position' column.")
#     print("Column Index:", df.columns.get_loc("name_position"))
#     print("First Valid Index:", df['name_position'].first_valid_index())

# if not found:
#   print("No DataFrame contains the 'name_position' column.")
# else:
#     print(f"DataFrame '{df_name}' does not contain the 'name_position' column.")

In [66]:
csv_dataframes_normalized = csv_dataframes.copy()

###Promote row to header

In [67]:
def promote_row_to_header(df, keyword="name_position"):
    """
    Find the first row containing the keyword and promote it to header.
    Keeps data intact, deletes rows above header row.
    """
    import pandas as pd

    # convert to string for matching, safe handling of NaN
    match_df = df.astype(str).apply(lambda col: col.str.lower())

    # detect first row that contains keyword
    header_row_index = None
    for i, row in match_df.iterrows():
        if keyword in row.values:
            header_row_index = i
            break

    # if no row contains keyword, return unchanged
    if header_row_index is None:
        return df.copy()

    # extract header names
    new_cols = df.iloc[header_row_index].astype(str).tolist()

    # apply header + trim data
    trimmed_df = df.iloc[header_row_index + 1:].copy()
    trimmed_df.columns = new_cols

    return trimmed_df.reset_index(drop=True)

In [68]:
for name, df in csv_dataframes.items():
    new_df = promote_row_to_header(df, keyword="name_position")
    csv_dataframes[name] = new_df

### Displaying the first 5 rows of each loaded DataFrame:

In [69]:
for df_name, df in csv_dataframes.items():
    print(f"\n--- DataFrame: {df_name} ---")
    # df = df.replace({$}as())) # This line caused a SyntaxError and has been commented out
    display(df.head())


--- DataFrame: AZPN_2022-10-28_SCT_table2 ---


name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
4                      NaN                      NaN                      NaN   
6     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   

  fiscal_year fiscal_year fiscal_year  salary  salary  salary stock_awards  \
1        2022        2022        2022  468750  468750  468750      7800162   
2        2021        2021        2021  600000  600000  600000      4649941   
3        2020        2020        2020  600000  600000  600000           --   
4        2019        2019        2019  586186  586186  586186      4650012   
6        2022        2022        2022  318750  318750  318750       637545   

   ... non_equity_incentive all_other_comp all_other_comp all_other_comp  \
1  ...               600000           7175           7175           7175   
2  ...               320000           9273           9273           9273   
3  ...               713920           8211           8211           8211   
4  ...               721990           8967           8967           8967   
6  ...               225000           7509           7509           7509   

      total     total     total  nan  nan  nan  
1  14942013  14942013  14942013  NaN  NaN  NaN  
2   8418919   8418919   8418919  NaN  NaN  NaN  
3   1322131   1322131   1322131  NaN  NaN  NaN  
4   7621337   7621337   7621337  NaN  NaN  NaN  
6   1188804   1188804   1188804  NaN  NaN  NaN  

[5 rows x 27 columns]


--- DataFrame: AZPN_2022-10-28_SCT_table3 ---


name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

             name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

             name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

  fiscal_year  ... all_other_comp     total     total     total     total  \
1        2022  ...           9567  22635094  22635094  22635094  22635094   
2        2021  ...           9273   8418919   8418919   8418919   8418919   
3        2020  ...           8211   7626325   7626325   7626325   7626325   
5        2022  ...          10012   3802126   3802126   3802126   3802126   
6        2021  ...           6120   3020456   3020456   3020456   3020456   

      total     total     total     total     total  
1  22635094  22635094  22635094  22635094  22635094  
2   8418919   8418919   8418919   8418919   8418919  
3   7626325   7626325   7626325   7626325   7626325  
5   3802126   3802126   3802126   3802126   3802126  
6   3020456   3020456   3020456   3020456   3020456  

[5 rows x 72 columns]


--- DataFrame: AZPN_2023-10-24_SCT ---


...

name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position fiscal_year fiscal_year  \
1           Nicholas Swenson Chief Executive Officer        2020        2020   
2           Nicholas Swenson Chief Executive Officer        2019        2019   
4           Brian Ochocki(1) Chief Financial Officer        2020        2020   
5           Brian Ochocki(1) Chief Financial Officer        2019        2019   
7  Brett A. Reynolds(3) Former Chief Financial Of...        2020        2020   

  fiscal_year  salary  salary  salary   bonus  ... non_equity_incentive  \
1        2020   50000   50000   50000  250(2)  ...                    0   
2        2019   50000   50000   50000       0  ...                    0   
4        2020  161000  161000  161000  250(2)  ...                    0   
5        2019      --      --      --      --  ...                   --   
7        2020   10000   10000   10000       0  ...                    0   

  pension_value pension_value pension_value all_other_comp all_other_comp  \
1             0             0             0              0              0   
2             0             0             0              0              0   
4             0             0             0              0              0   
5            --            --            --             --             --   
7             0             0             0          42000          42000   

  all_other_comp   total   total   total  
1              0   50250   50250   50250  
2              0   50000   50000   50000  
4              0  161250  161250  161250  
5             --      --      --      --  
7          42000   52000   52000   52000  

[5 rows x 24 columns]


--- DataFrame: AIRT_2014-07-18_SCT ---


name_position fiscal_year  salary  \
0  nicholas_j_swenson_interim_chief_executive_off...        2014           
1                                         john_parry        2014  187200   
2  former_vice_president_finance_chief_financial_...        2013  179200   
3                                  william_h_simpson        2014  254600   
4              executive_vice_president_and_director        2013  249700   

  option_awards non_equity_incentive pension_value all_other_comp  nan   total  
0                                                           17000        17000  
1                              47350                        17448       251998  
2                              46723                        15690  NaN  241613  
3                              63133                        17987       335720  
4                              62297                        19469  NaN  331466


--- DataFrame: AIRT_2022-07-05_SCT ---


name_position  \
0                                       NaN   
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position  \
0                                       NaN   
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position fiscal_year fiscal_year  \
0                                       NaN         NaN         NaN   
2  Nicholas Swenson Chief Executive Officer        2022        2022   
3  Nicholas Swenson Chief Executive Officer        2021        2021   
5     Brian Ochocki Chief Financial Officer        2022        2022   
6     Brian Ochocki Chief Financial Officer        2021        2021   

  fiscal_year  salary  salary  salary   bonus  ... equity_compensation  \
0         NaN     NaN     NaN     NaN     NaN  ...    Option Awards(1)   
2        2022   50000   50000   50000       0  ...              781595   
3        2021   50000   50000   50000     250  ...                   0   
5        2022  248000  248000  248000  105500  ...               97699   
6        2021  231000  231000  231000   20250  ...                   0   

  non_equity_incentive non_equity_incentive non_equity_incentive  \
0                  NaN                  NaN                  NaN   
2                    0                    0                    0   
3                    0                    0                    0   
5                    0                    0                    0   
6                    0                    0                    0   

  all_other_comp all_other_comp all_other_comp   total   total   total  
0            NaN            NaN            NaN     NaN     NaN     NaN  
2              0              0              0  831595  831595  831595  
3              0              0              0   50250   50250   50250  
5              0              0              0  451199  451199  451199  
6              0              0              0  251250  251250  251250  

[5 rows x 27 columns]

### Locate and Trim DataFrames

### Subtask:
For each DataFrame in `csv_dataframes`, identify the index of the `name_position` column and the first row where a non-NaN value appears in that column. Then, trim the DataFrame to include only data from that row and column onwards.


**Reasoning**:
The subtask requires iterating through each DataFrame, identifying the 'name_position' column, finding the first non-NaN value in it, and then trimming the DataFrame from that row and column onwards. The provided code implements this logic by using `first_valid_index()` for rows and `get_loc()` for columns, then slicing the DataFrame accordingly.



In [70]:
for df_name, df in csv_dataframes.items():
    if 'name_position' in df.columns:
        first_valid_row_index = df['name_position'].first_valid_index()
        if first_valid_row_index is not None:
            # Get the positional index of the first 'name_position' column
            name_position_col_index = list(df.columns).index('name_position')

            # Trim rows from first_valid_row_index onwards
            trimmed_df = df.loc[first_valid_row_index:].copy()

            # Trim columns from name_position_col_index onwards
            trimmed_df = trimmed_df.iloc[:, name_position_col_index:].copy()

            csv_dataframes[df_name] = trimmed_df
            print(f"DataFrame '{df_name}' trimmed successfully. First 5 rows:\n")
            display(csv_dataframes[df_name].head())
        else:
            print(f"DataFrame '{df_name}': 'name_position' column contains no valid non-NaN values. Skipping trimming.\n")
    else:
        print(f"DataFrame '{df_name}' does not contain 'name_position' column. Skipping trimming.\n")

DataFrame 'AZPN_2022-10-28_SCT_table2' trimmed successfully. First 5 rows:



name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
4                      NaN                      NaN                      NaN   
6     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   

  fiscal_year fiscal_year fiscal_year  salary  salary  salary stock_awards  \
1        2022        2022        2022  468750  468750  468750      7800162   
2        2021        2021        2021  600000  600000  600000      4649941   
3        2020        2020        2020  600000  600000  600000           --   
4        2019        2019        2019  586186  586186  586186      4650012   
6        2022        2022        2022  318750  318750  318750       637545   

   ... non_equity_incentive all_other_comp all_other_comp all_other_comp  \
1  ...               600000           7175           7175           7175   
2  ...               320000           9273           9273           9273   
3  ...               713920           8211           8211           8211   
4  ...               721990           8967           8967           8967   
6  ...               225000           7509           7509           7509   

      total     total     total  nan  nan  nan  
1  14942013  14942013  14942013  NaN  NaN  NaN  
2   8418919   8418919   8418919  NaN  NaN  NaN  
3   1322131   1322131   1322131  NaN  NaN  NaN  
4   7621337   7621337   7621337  NaN  NaN  NaN  
6   1188804   1188804   1188804  NaN  NaN  NaN  

[5 rows x 27 columns]

DataFrame 'AZPN_2022-10-28_SCT_table3' trimmed successfully. First 5 rows:



name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

             name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

             name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

  fiscal_year  ... all_other_comp     total     total     total     total  \
1        2022  ...           9567  22635094  22635094  22635094  22635094   
2        2021  ...           9273   8418919   8418919   8418919   8418919   
3        2020  ...           8211   7626325   7626325   7626325   7626325   
5        2022  ...          10012   3802126   3802126   3802126   3802126   
6        2021  ...           6120   3020456   3020456   3020456   3020456   

      total     total     total     total     total  
1  22635094  22635094  22635094  22635094  22635094  
2   8418919   8418919   8418919   8418919   8418919  
3   7626325   7626325   7626325   7626325   7626325  
5   3802126   3802126   3802126   3802126   3802126  
6   3020456   3020456   3020456   3020456   3020456  

[5 rows x 72 columns]

DataFrame 'AZPN_2023-10-24_SCT' trimmed successfully. First 5 rows:



...

name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position fiscal_year fiscal_year  \
1           Nicholas Swenson Chief Executive Officer        2020        2020   
2           Nicholas Swenson Chief Executive Officer        2019        2019   
4           Brian Ochocki(1) Chief Financial Officer        2020        2020   
5           Brian Ochocki(1) Chief Financial Officer        2019        2019   
7  Brett A. Reynolds(3) Former Chief Financial Of...        2020        2020   

  fiscal_year  salary  salary  salary   bonus  ... non_equity_incentive  \
1        2020   50000   50000   50000  250(2)  ...                    0   
2        2019   50000   50000   50000       0  ...                    0   
4        2020  161000  161000  161000  250(2)  ...                    0   
5        2019      --      --      --      --  ...                   --   
7        2020   10000   10000   10000       0  ...                    0   

  pension_value pension_value pension_value all_other_comp all_other_comp  \
1             0             0             0              0              0   
2             0             0             0              0              0   
4             0             0             0              0              0   
5            --            --            --             --             --   
7             0             0             0          42000          42000   

  all_other_comp   total   total   total  
1              0   50250   50250   50250  
2              0   50000   50000   50000  
4              0  161250  161250  161250  
5             --      --      --      --  
7          42000   52000   52000   52000  

[5 rows x 24 columns]

DataFrame 'AIRT_2014-07-18_SCT' trimmed successfully. First 5 rows:



name_position fiscal_year  salary  \
0  nicholas_j_swenson_interim_chief_executive_off...        2014           
1                                         john_parry        2014  187200   
2  former_vice_president_finance_chief_financial_...        2013  179200   
3                                  william_h_simpson        2014  254600   
4              executive_vice_president_and_director        2013  249700   

  option_awards non_equity_incentive pension_value all_other_comp  nan   total  
0                                                           17000        17000  
1                              47350                        17448       251998  
2                              46723                        15690  NaN  241613  
3                              63133                        17987       335720  
4                              62297                        19469  NaN  331466

DataFrame 'AIRT_2022-07-05_SCT' trimmed successfully. First 5 rows:



name_position  \
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position  \
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position fiscal_year fiscal_year  \
2  Nicholas Swenson Chief Executive Officer        2022        2022   
3  Nicholas Swenson Chief Executive Officer        2021        2021   
5     Brian Ochocki Chief Financial Officer        2022        2022   
6     Brian Ochocki Chief Financial Officer        2021        2021   

  fiscal_year  salary  salary  salary   bonus  ... equity_compensation  \
2        2022   50000   50000   50000       0  ...              781595   
3        2021   50000   50000   50000     250  ...                   0   
5        2022  248000  248000  248000  105500  ...               97699   
6        2021  231000  231000  231000   20250  ...                   0   

  non_equity_incentive non_equity_incentive non_equity_incentive  \
2                    0                    0                    0   
3                    0                    0                    0   
5                    0                    0                    0   
6                    0                    0                    0   

  all_other_comp all_other_comp all_other_comp   total   total   total  
2              0              0              0  831595  831595  831595  
3              0              0              0   50250   50250   50250  
5              0              0              0  451199  451199  451199  
6              0              0              0  251250  251250  251250  

[4 rows x 27 columns]

**Reasoning**:
The `TypeError` arises because `df.columns.get_loc('name_position')` can return a boolean array (if multiple columns are named 'name_position') or a slice, which `iloc` does not directly support for column indexing in the format `iloc[:, boolean_array]`. To fix this, I need to ensure `name_position_col_index` is always a single integer representing the positional index of the first occurrence of the 'name_position' column. Using `list(df.columns).index('name_position')` achieves this reliably.



### Displaying the first 5 rows of each loaded DataFrame:

In [71]:
for df_name, df in csv_dataframes.items():
    print(f"\n--- DataFrame: {df_name} ---")
    # df = df.replace({$}as())) # This line caused a SyntaxError and has been commented out
    display(df.head())


--- DataFrame: AZPN_2022-10-28_SCT_table2 ---


name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
4                      NaN                      NaN                      NaN   
6     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   

  fiscal_year fiscal_year fiscal_year  salary  salary  salary stock_awards  \
1        2022        2022        2022  468750  468750  468750      7800162   
2        2021        2021        2021  600000  600000  600000      4649941   
3        2020        2020        2020  600000  600000  600000           --   
4        2019        2019        2019  586186  586186  586186      4650012   
6        2022        2022        2022  318750  318750  318750       637545   

   ... non_equity_incentive all_other_comp all_other_comp all_other_comp  \
1  ...               600000           7175           7175           7175   
2  ...               320000           9273           9273           9273   
3  ...               713920           8211           8211           8211   
4  ...               721990           8967           8967           8967   
6  ...               225000           7509           7509           7509   

      total     total     total  nan  nan  nan  
1  14942013  14942013  14942013  NaN  NaN  NaN  
2   8418919   8418919   8418919  NaN  NaN  NaN  
3   1322131   1322131   1322131  NaN  NaN  NaN  
4   7621337   7621337   7621337  NaN  NaN  NaN  
6   1188804   1188804   1188804  NaN  NaN  NaN  

[5 rows x 27 columns]


--- DataFrame: AZPN_2022-10-28_SCT_table3 ---


name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

             name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

             name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

  fiscal_year  ... all_other_comp     total     total     total     total  \
1        2022  ...           9567  22635094  22635094  22635094  22635094   
2        2021  ...           9273   8418919   8418919   8418919   8418919   
3        2020  ...           8211   7626325   7626325   7626325   7626325   
5        2022  ...          10012   3802126   3802126   3802126   3802126   
6        2021  ...           6120   3020456   3020456   3020456   3020456   

      total     total     total     total     total  
1  22635094  22635094  22635094  22635094  22635094  
2   8418919   8418919   8418919   8418919   8418919  
3   7626325   7626325   7626325   7626325   7626325  
5   3802126   3802126   3802126   3802126   3802126  
6   3020456   3020456   3020456   3020456   3020456  

[5 rows x 72 columns]


--- DataFrame: AZPN_2023-10-24_SCT ---


...

name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position fiscal_year fiscal_year  \
1           Nicholas Swenson Chief Executive Officer        2020        2020   
2           Nicholas Swenson Chief Executive Officer        2019        2019   
4           Brian Ochocki(1) Chief Financial Officer        2020        2020   
5           Brian Ochocki(1) Chief Financial Officer        2019        2019   
7  Brett A. Reynolds(3) Former Chief Financial Of...        2020        2020   

  fiscal_year  salary  salary  salary   bonus  ... non_equity_incentive  \
1        2020   50000   50000   50000  250(2)  ...                    0   
2        2019   50000   50000   50000       0  ...                    0   
4        2020  161000  161000  161000  250(2)  ...                    0   
5        2019      --      --      --      --  ...                   --   
7        2020   10000   10000   10000       0  ...                    0   

  pension_value pension_value pension_value all_other_comp all_other_comp  \
1             0             0             0              0              0   
2             0             0             0              0              0   
4             0             0             0              0              0   
5            --            --            --             --             --   
7             0             0             0          42000          42000   

  all_other_comp   total   total   total  
1              0   50250   50250   50250  
2              0   50000   50000   50000  
4              0  161250  161250  161250  
5             --      --      --      --  
7          42000   52000   52000   52000  

[5 rows x 24 columns]


--- DataFrame: AIRT_2014-07-18_SCT ---


name_position fiscal_year  salary  \
0  nicholas_j_swenson_interim_chief_executive_off...        2014           
1                                         john_parry        2014  187200   
2  former_vice_president_finance_chief_financial_...        2013  179200   
3                                  william_h_simpson        2014  254600   
4              executive_vice_president_and_director        2013  249700   

  option_awards non_equity_incentive pension_value all_other_comp  nan   total  
0                                                           17000        17000  
1                              47350                        17448       251998  
2                              46723                        15690  NaN  241613  
3                              63133                        17987       335720  
4                              62297                        19469  NaN  331466


--- DataFrame: AIRT_2022-07-05_SCT ---


name_position  \
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position  \
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position fiscal_year fiscal_year  \
2  Nicholas Swenson Chief Executive Officer        2022        2022   
3  Nicholas Swenson Chief Executive Officer        2021        2021   
5     Brian Ochocki Chief Financial Officer        2022        2022   
6     Brian Ochocki Chief Financial Officer        2021        2021   

  fiscal_year  salary  salary  salary   bonus  ... equity_compensation  \
2        2022   50000   50000   50000       0  ...              781595   
3        2021   50000   50000   50000     250  ...                   0   
5        2022  248000  248000  248000  105500  ...               97699   
6        2021  231000  231000  231000   20250  ...                   0   

  non_equity_incentive non_equity_incentive non_equity_incentive  \
2                    0                    0                    0   
3                    0                    0                    0   
5                    0                    0                    0   
6                    0                    0                    0   

  all_other_comp all_other_comp all_other_comp   total   total   total  
2              0              0              0  831595  831595  831595  
3              0              0              0   50250   50250   50250  
5              0              0              0  451199  451199  451199  
6              0              0              0  251250  251250  251250  

[4 rows x 27 columns]

## Task
Locate the `name_position` column in each DataFrame within `csv_dataframes` and identify the first row with a non-NaN value in that column. Trim each DataFrame to retain only data from that identified row and `name_position` column onwards. Finally, display the first 5 rows of each trimmed DataFrame.

## Display Trimmed DataFrames

### Subtask:
Display the first 5 rows of each DataFrame after trimming to confirm the data has been correctly isolated.


In [72]:
for df_name, df in csv_dataframes.items():
    print(f"\n--- Trimmed DataFrame: {df_name} ---")
    display(df.head())


--- Trimmed DataFrame: AZPN_2022-10-28_SCT_table2 ---


name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
4                      NaN                      NaN                      NaN   
6     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   

  fiscal_year fiscal_year fiscal_year  salary  salary  salary stock_awards  \
1        2022        2022        2022  468750  468750  468750      7800162   
2        2021        2021        2021  600000  600000  600000      4649941   
3        2020        2020        2020  600000  600000  600000           --   
4        2019        2019        2019  586186  586186  586186      4650012   
6        2022        2022        2022  318750  318750  318750       637545   

   ... non_equity_incentive all_other_comp all_other_comp all_other_comp  \
1  ...               600000           7175           7175           7175   
2  ...               320000           9273           9273           9273   
3  ...               713920           8211           8211           8211   
4  ...               721990           8967           8967           8967   
6  ...               225000           7509           7509           7509   

      total     total     total  nan  nan  nan  
1  14942013  14942013  14942013  NaN  NaN  NaN  
2   8418919   8418919   8418919  NaN  NaN  NaN  
3   1322131   1322131   1322131  NaN  NaN  NaN  
4   7621337   7621337   7621337  NaN  NaN  NaN  
6   1188804   1188804   1188804  NaN  NaN  NaN  

[5 rows x 27 columns]


--- Trimmed DataFrame: AZPN_2022-10-28_SCT_table3 ---


name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

             name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

             name_position            name_position            name_position  \
1        Antonio J. Pietri        Antonio J. Pietri        Antonio J. Pietri   
2            President and            President and            President and   
3  Chief Executive Officer  Chief Executive Officer  Chief Executive Officer   
5     Chantelle Breithaupt     Chantelle Breithaupt     Chantelle Breithaupt   
6    Senior Vice President    Senior Vice President    Senior Vice President   

  fiscal_year  ... all_other_comp     total     total     total     total  \
1        2022  ...           9567  22635094  22635094  22635094  22635094   
2        2021  ...           9273   8418919   8418919   8418919   8418919   
3        2020  ...           8211   7626325   7626325   7626325   7626325   
5        2022  ...          10012   3802126   3802126   3802126   3802126   
6        2021  ...           6120   3020456   3020456   3020456   3020456   

      total     total     total     total     total  
1  22635094  22635094  22635094  22635094  22635094  
2   8418919   8418919   8418919   8418919   8418919  
3   7626325   7626325   7626325   7626325   7626325  
5   3802126   3802126   3802126   3802126   3802126  
6   3020456   3020456   3020456   3020456   3020456  

[5 rows x 72 columns]


--- Trimmed DataFrame: AZPN_2023-10-24_SCT ---


...

name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position fiscal_year fiscal_year  \
1           Nicholas Swenson Chief Executive Officer        2020        2020   
2           Nicholas Swenson Chief Executive Officer        2019        2019   
4           Brian Ochocki(1) Chief Financial Officer        2020        2020   
5           Brian Ochocki(1) Chief Financial Officer        2019        2019   
7  Brett A. Reynolds(3) Former Chief Financial Of...        2020        2020   

  fiscal_year  salary  salary  salary   bonus  ... non_equity_incentive  \
1        2020   50000   50000   50000  250(2)  ...                    0   
2        2019   50000   50000   50000       0  ...                    0   
4        2020  161000  161000  161000  250(2)  ...                    0   
5        2019      --      --      --      --  ...                   --   
7        2020   10000   10000   10000       0  ...                    0   

  pension_value pension_value pension_value all_other_comp all_other_comp  \
1             0             0             0              0              0   
2             0             0             0              0              0   
4             0             0             0              0              0   
5            --            --            --             --             --   
7             0             0             0          42000          42000   

  all_other_comp   total   total   total  
1              0   50250   50250   50250  
2              0   50000   50000   50000  
4              0  161250  161250  161250  
5             --      --      --      --  
7          42000   52000   52000   52000  

[5 rows x 24 columns]


--- Trimmed DataFrame: AIRT_2014-07-18_SCT ---


name_position fiscal_year  salary  \
0  nicholas_j_swenson_interim_chief_executive_off...        2014           
1                                         john_parry        2014  187200   
2  former_vice_president_finance_chief_financial_...        2013  179200   
3                                  william_h_simpson        2014  254600   
4              executive_vice_president_and_director        2013  249700   

  option_awards non_equity_incentive pension_value all_other_comp  nan   total  
0                                                           17000        17000  
1                              47350                        17448       251998  
2                              46723                        15690  NaN  241613  
3                              63133                        17987       335720  
4                              62297                        19469  NaN  331466


--- Trimmed DataFrame: AIRT_2022-07-05_SCT ---


name_position  \
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position  \
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position fiscal_year fiscal_year  \
2  Nicholas Swenson Chief Executive Officer        2022        2022   
3  Nicholas Swenson Chief Executive Officer        2021        2021   
5     Brian Ochocki Chief Financial Officer        2022        2022   
6     Brian Ochocki Chief Financial Officer        2021        2021   

  fiscal_year  salary  salary  salary   bonus  ... equity_compensation  \
2        2022   50000   50000   50000       0  ...              781595   
3        2021   50000   50000   50000     250  ...                   0   
5        2022  248000  248000  248000  105500  ...               97699   
6        2021  231000  231000  231000   20250  ...                   0   

  non_equity_incentive non_equity_incentive non_equity_incentive  \
2                    0                    0                    0   
3                    0                    0                    0   
5                    0                    0                    0   
6                    0                    0                    0   

  all_other_comp all_other_comp all_other_comp   total   total   total  
2              0              0              0  831595  831595  831595  
3              0              0              0   50250   50250   50250  
5              0              0              0  451199  451199  451199  
6              0              0              0  251250  251250  251250  

[4 rows x 27 columns]

##Copying the dataframe list for post processing

###fix split headers

it merges columns with same name

In [ ]:
def fix_two_row_header(df):
    first_row = df.iloc[0].astype(str).str.lower().tolist()
    col_names = df.columns.astype(str).str.lower().tolist()

    matches = sum([1 for x in first_row if x in col_names])
    if matches < 2:
        return df

    new_cols = []
    for old, new in zip(df.columns, df.iloc[0]):

        new = str(new).strip().lower()
        old = str(old).strip().lower()

        # ---- RULE 1: if new == old → use one version only ----
        if new == old:
            new_cols.append(old)
            continue

        # ---- RULE 2: keep non-empty replacement logic ----
        if new in ("nan", "", None):
            new_cols.append(old)
            continue

        if old in ("nan", "", None):
            new_cols.append(new)
            continue

        # ---- RULE 3: avoid doubling patterns like "salary_salary" ----
        if new in old:
            new_cols.append(old)
            continue

        if old in new:
            new_cols.append(new)
            continue

        # ---- RULE 4: safe merge fallback ----
        new_cols.append(f"{old}_{new}")

    df.columns = new_cols
    df = df.iloc[1:].reset_index(drop=True)

    return df

In [ ]:
for name, df in csv_dataframes.items():
    fixed = fix_two_row_header(df.copy())
    csv_dataframes[name] = fixed
    print(f"Repaired header split in: {name}")

Repaired header split in: AZPN_2022-10-28_SCT_table2
Repaired header split in: AZPN_2022-10-28_SCT_table3
Repaired header split in: AZPN_2023-10-24_SCT
Repaired header split in: AZPN_2024-10-24_SCT
Repaired header split in: AZPN_2022-10-28_SCT_table1
Repaired header split in: AIRT_2025-07-03_SCT
Repaired header split in: AIRT_2023-07-24_SCT
Repaired header split in: AIRT_2009-07-15_SCT
Repaired header split in: AIRT_2005-08-12_SCT
Repaired header split in: AIRT_2024-07-10_SCT
Repaired header split in: AIRT_2015-07-22_SCT
Repaired header split in: AIRT_2012-07-20_SCT
Repaired header split in: AIRT_2008-08-14_SCT
Repaired header split in: AIRT_2007-08-13_SCT
Repaired header split in: AIRT_2013-07-22_SCT
Repaired header split in: AIRT_2011-07-15_SCT
Repaired header split in: AIRT_2021-07-19_SCT
Repaired header split in: AIRT_2020-07-20_SCT
Repaired header split in: AIRT_2014-07-18_SCT
Repaired header split in: AIRT_2022-07-05_SCT


###Expand the _ column

In [ ]:
for df_name, df in csv_dataframes_normalized.items():
    print(f"\n--- cleaned DataFrame: {df_name} ---")
    display(df)


--- cleaned DataFrame: AZPN_2022-10-28_SCT_table2 ---


name_position_antonio j. pietri  \
0                                       President and   
1                             Chief Executive Officer   
2                                                 NaN   
3                                Chantelle Breithaupt   
4                           Senior Vice President and   
5                             Chief Financial Officer   
6                                       Manish Chawla   
7   Executive Vice President and Chief Revenue Off...   
8                                 Frederic G. Hammond   
9   Senior Vice President, General Counsel and Sec...   
10                                                NaN   
11                                                NaN   
12  (1) Amounts shown represent aggregate grant da...   
13  (2) Prior to the Closing of the Emerson Transa...   
14  (3) Amounts shown include matching contributio...   
15                                                NaN   
16  (4) Mr. Chawla was appointed as our Executive ...   

                      name_position_antonio j. pietri  \
0                                       President and   
1                             Chief Executive Officer   
2                                                 NaN   
3                                Chantelle Breithaupt   
4                           Senior Vice President and   
5                             Chief Financial Officer   
6                                       Manish Chawla   
7   Executive Vice President and Chief Revenue Off...   
8                                 Frederic G. Hammond   
9   Senior Vice President, General Counsel and Sec...   
10                                                NaN   
11                                                NaN   
12  (1) Amounts shown represent aggregate grant da...   
13  (2) Prior to the Closing of the Emerson Transa...   
14  (3) Amounts shown include matching contributio...   
15                                                NaN   
16  (4) Mr. Chawla was appointed as our Executive ...   

                      name_position_antonio j. pietri  \
0                                       President and   
1                             Chief Executive Officer   
2                                                 NaN   
3                                Chantelle Breithaupt   
4                           Senior Vice President and   
5                             Chief Financial Officer   
6                                       Manish Chawla   
7   Executive Vice President and Chief Revenue Off...   
8                                 Frederic G. Hammond   
9   Senior Vice President, General Counsel and Sec...   
10                                                NaN   
11                                                NaN   
12  (1) Amounts shown represent aggregate grant da...   
13  (2) Prior to the Closing of the Emerson Transa...   
14  (3) Amounts shown include matching contributio...   
15                                                NaN   
16  (4) Mr. Chawla was appointed as our Executive ...   

                                     fiscal_year_2022  \
0                                                2021   
1                                                2020   
2                                                2019   
3                                                2022   
4                                                2021   
5                                                 NaN   
6                                                2022   
7                                                 NaN   
8                                                2022   
9                                                2021   
10                                               2020   
11                                               2019   
12  (1) Amounts shown represent aggregate grant da...   
13  (2) Prior to the Closing of the Emerson Transa...   
14  (3) Amounts shown include matching contributio...   
15  (2) Prior to the Closing 


--- cleaned DataFrame: AZPN_2022-10-28_SCT_table3 ---


name_position  \
1                                   Antonio J. Pietri   
2                                       President and   
3                             Chief Executive Officer   
5                                Chantelle Breithaupt   
6                               Senior Vice President   
7                         and Chief Financial Officer   
9                                       Manish Chawla   
10                           Executive Vice President   
11                          and Chief Revenue Officer   
13                                Frederic G. Hammond   
14                             Senior Vice President,   
15                      General Counsel and Secretary   
18  (1) Amounts shown represent aggregate grant da...   
19  (1) Amounts shown represent aggregate grant da...   
20  (1) Amounts shown represent aggregate grant da...   
21  (1) Amounts shown represent aggregate grant da...   
23  (2) Amounts shown consist of awards based on p...   
24  (2) Amounts shown consist of awards based on p...   
26  (3) Amounts shown include matching contributio...   
27  (3) Amounts shown include matching contributio...   
29  (4) Mr. Chawla was appointed as our Executive ...   

                                        name_position  \
1                                   Antonio J. Pietri   
2                                       President and   
3                             Chief Executive Officer   
5                                Chantelle Breithaupt   
6                               Senior Vice President   
7                         and Chief Financial Officer   
9                                       Manish Chawla   
10                           Executive Vice President   
11                          and Chief Revenue Officer   
13                                Frederic G. Hammond   
14                             Senior Vice President,   
15                      General Counsel and Secretary   
18  (1) Amounts shown represent aggregate grant da...   
19  (1) Amounts shown represent aggregate grant da...   
20  (1) Amounts shown represent aggregate grant da...   
21  (1) Amounts shown represent aggregate grant da...   
23  (2) Amounts shown consist of awards based on p...   
24  (2) Amounts shown consist of awards based on p...   
26  (3) Amounts shown include matching contributio...   
27  (3) Amounts shown include matching contributio...   
29  (4) Mr. Chawla was appointed as our Executive ...   

                                        name_position  \
1                                   Antonio J. Pietri   
2                                       President and   
3                             Chief Executive Officer   
5                                Chantelle Breithaupt   
6                               Senior Vice President   
7                         and Chief Financial Officer   
9                                       Manish Chawla   
10                           Executive Vice President   
11                          and Chief Revenue Officer   
13                                Frederic G. Hammond   
14                             Senior Vice President,   
15                      General Counsel and Secretary   
18  (1) Amounts shown represent aggregate grant da...   
19  (1) Amounts shown represent aggregate grant da...   
20  (1) Amounts shown represent aggregate grant da...   
21  (1) Amounts shown represent aggregate grant da...   
23  (2) Amounts shown consist of awards based on p...   
24  (2) Amounts shown consist of awards based on p...   
26  (3) Amounts shown include matching contributio...   
27  (3) Amounts shown include matching contributio...   
29  (4) Mr. Chawla was appointed as our Executive ...   

                                        name_position  \
1                                   Antonio J. Pietri   
2                                       President and   
3                             Chief Executive Officer   
5                                Chantelle Brei


--- cleaned DataFrame: AZPN_2023-10-24_SCT ---


...

name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   
8  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position  \
1           Nicholas Swenson Chief Executive Officer   
2           Nicholas Swenson Chief Executive Officer   
4           Brian Ochocki(1) Chief Financial Officer   
5           Brian Ochocki(1) Chief Financial Officer   
7  Brett A. Reynolds(3) Former Chief Financial Of...   
8  Brett A. Reynolds(3) Former Chief Financial Of...   

                                       name_position fiscal_year fiscal_year  \
1           Nicholas Swenson Chief Executive Officer        2020        2020   
2           Nicholas Swenson Chief Executive Officer        2019        2019   
4           Brian Ochocki(1) Chief Financial Officer        2020        2020   
5           Brian Ochocki(1) Chief Financial Officer        2019        2019   
7  Brett A. Reynolds(3) Former Chief Financial Of...        2020        2020   
8  Brett A. Reynolds(3) Former Chief Financial Of...        2019        2019   

  fiscal_year  salary  salary  salary   bonus  ... non_equity_incentive  \
1        2020   50000   50000   50000  250(2)  ...                    0   
2        2019   50000   50000   50000       0  ...                    0   
4        2020  161000  161000  161000  250(2)  ...                    0   
5        2019      --      --      --      --  ...                   --   
7        2020   10000   10000   10000       0  ...                    0   
8        2019  265000  265000  265000     150  ...                    0   

  pension_value pension_value pension_value all_other_comp all_other_comp  \
1             0             0             0              0              0   
2             0             0             0              0              0   
4             0             0             0              0              0   
5            --            --            --             --             --   
7             0             0             0          42000          42000   
8             0             0             0              0              0   

  all_other_comp   total   total   total  
1              0   50250   50250   50250  
2              0   50000   50000   50000  
4              0  161250  161250  161250  
5             --      --      --      --  
7          42000   52000   52000   52000  
8              0  265150  265150  265150  

[6 rows x 24 columns]


--- cleaned DataFrame: AIRT_2014-07-18_SCT ---


name_position fiscal_year  salary  \
0  nicholas_j_swenson_interim_chief_executive_off...        2014           
1                                         john_parry        2014  187200   
2  former_vice_president_finance_chief_financial_...        2013  179200   
3                                  william_h_simpson        2014  254600   
4              executive_vice_president_and_director        2013  249700   
5                                       walter_clark        2014  181900   
6        former_chief_executive_officer_and_director        2013  256000   

  option_awards non_equity_incentive pension_value all_other_comp  nan   total  
0                                                           17000        17000  
1                              47350                        17448       251998  
2                              46723                        15690  NaN  241613  
3                              63133                        17987       335720  
4                              62297                        19469  NaN  331466  
5                              36121                       592709       810730  
6                              62297                        25591  NaN  343888


--- cleaned DataFrame: AIRT_2022-07-05_SCT ---


name_position  \
0                                       NaN   
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position  \
0                                       NaN   
2  Nicholas Swenson Chief Executive Officer   
3  Nicholas Swenson Chief Executive Officer   
5     Brian Ochocki Chief Financial Officer   
6     Brian Ochocki Chief Financial Officer   

                              name_position fiscal_year fiscal_year  \
0                                       NaN         NaN         NaN   
2  Nicholas Swenson Chief Executive Officer        2022        2022   
3  Nicholas Swenson Chief Executive Officer        2021        2021   
5     Brian Ochocki Chief Financial Officer        2022        2022   
6     Brian Ochocki Chief Financial Officer        2021        2021   

  fiscal_year  salary  salary  salary   bonus  ... equity_compensation  \
0         NaN     NaN     NaN     NaN     NaN  ...    Option Awards(1)   
2        2022   50000   50000   50000       0  ...              781595   
3        2021   50000   50000   50000     250  ...                   0   
5        2022  248000  248000  248000  105500  ...               97699   
6        2021  231000  231000  231000   20250  ...                   0   

  non_equity_incentive non_equity_incentive non_equity_incentive  \
0                  NaN                  NaN                  NaN   
2                    0                    0                    0   
3                    0                    0                    0   
5                    0                    0                    0   
6                    0                    0                    0   

  all_other_comp all_other_comp all_other_comp   total   total   total  
0            NaN            NaN            NaN     NaN     NaN     NaN  
2              0              0              0  831595  831595  831595  
3              0              0              0   50250   50250   50250  
5              0              0              0  451199  451199  451199  
6              0              0              0  251250  251250  251250  

[5 rows x 27 columns]

In [ ]:
def merge_duplicate_cols(df):
    # convert blanks to NaN
    df = df.replace(["", " "], np.nan)

    merged = {}

    for col in df.columns.unique():
        subset = df.filter(regex=f"^{col}$")
        merged[col] = subset.bfill(axis=1).iloc[:, 0]

    return pd.DataFrame(merged)

for df_name, df in csv_dataframes_normalized.items():
    df = merge_duplicate_cols(df)
    csv_dataframes_normalized[df_name] = df

/tmp/ipython-input-1438140441.py:3: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df = df.replace(["", " "], np.nan)


IndexError: single positional indexer is out-of-bounds

In [ ]:
# from pandas.api.types import is_numeric_dtype

# expanded_tables = {}

# for df_name, df in csv_dataframes_normalized.items():

#     if "fiscal_year" not in df.columns:
#         expanded_tables[df_name] = df.copy()
#         continue

#     new_rows = []

#     for _, row in df.iterrows():

#         fiscal_years = str(row["fiscal_year"]).split("_")
#         n = len(fiscal_years)

#         for i in range(n):
#             new_row = {}

#             # keep name_position as-is (repeat, don't split)
#             new_row["name_position"] = row["name_position"]

#             # assign fiscal year value
#             new_row["fiscal_year"] = fiscal_years[i]

#             # expand remaining columns
#             for col in df.columns:
#                 if col in ["name_position", "fiscal_year"]:
#                     continue

#                 val = row[col]

#                 # if entry is "123_456_789"
#                 if isinstance(val, str) and "_" in val:
#                     parts = val.split("_")
#                     new_row[col] = parts[i] if i < len(parts) else None

#                 else:
#                     # replicate value across expanded rows
#                     new_row[col] = val

#             new_rows.append(new_row)

#     expanded_tables[df_name] = pd.DataFrame(new_rows)

In [ ]:
# expanded_tables = {}

# for name, df in csv_dataframes_normalized.items():
#     expanded_tables[name] = expand_sct_smart(df)
#     print(f"{name}: {len(df)} → {len(expanded_tables[name])}")

In [ ]:
# for df_name, df in expanded_tables.items():
#     print(f"\n--- cleaned DataFrame: {df_name} ---")
#     display(df)

In [ ]:
for df_name, df in csv_dataframes_normalized.items():
    print(f"\n--- cleaned DataFrame: {df_name} ---")
    display(df)